In [1]:
!pip install optuna entmax

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 364.4/364.4 kB 8.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 233.5/233.5 kB 25.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.6/78.6 kB 8.8 MB/s eta 0:00:00


In [2]:
import numpy as np
import pandas as pd
from xgboost import XGBClassifier
from sklearn.model_selection import cross_validate, train_test_split
from sklearn.metrics import accuracy_score, matthews_corrcoef, make_scorer
from scipy.stats import shapiro
import optuna
from ncart import NCARClassifier

In [3]:
# This is a function that loads training and testing data for 10-fold cross validation
def prepare_train_test_dataset(datasets, test_idx):
  test_df = datasets[test_idx]
  train_df = pd.concat([datasets[i] for i in range(len(datasets)) if i != test_idx])

  X_train = train_df.iloc[:, 1:-1].values
  X_test = test_df.iloc[:, 1:-1].values
  y_train = train_df.iloc[:, -1].values
  y_test = test_df.iloc[:, -1].values

  return X_train, X_test, y_train, y_test

In [4]:
import torch

def train_with_base_ncart(datasets, key):
  print("Currently training NCART model with dataset key:", key)

  # Create a Pandas DataFrame to store all experiment results
  results_df = pd.DataFrame(columns=['Fold', 'Accuracy', 'MCC'])

  # Perform 10-fold cross validation
  dataset_list = datasets[key]

  for i in range(10):
    X_train, X_test, y_train, y_test = prepare_train_test_dataset(dataset_list, i)

    # Train the model
    model = NCARClassifier()
    model.fit(X=X_train, y=y_train, X_val=X_test, y_val=y_test)

    # Evaluate the model
    y_pred = model.predict(X_test)
    accuracy = accuracy_score(y_test, y_pred)
    mcc = matthews_corrcoef(y_test, y_pred)

    print("Fold", i+1, "Accuracy:", accuracy, "MCC:", mcc)
    results_df.loc[i] = [i+1, accuracy, mcc]

  return results_df

In [5]:
def create_objective_for_ncart(X_train, X_test, y_train, y_test):
  def objective(trial):
      # Suggest hyperparameters for GRANDE
      params = {
          "n_trees": trial.suggest_int("n_trees", 8, 128, step=8),
          "n_selected": trial.suggest_int("n_selected", 4, 32, step=4),
          "n_layers": trial.suggest_int("n_layers", 1, 8),
          "mask_type": trial.suggest_categorical("mask_type", ["sparsemax", "entmax"]),
      }

      base_model = NCARClassifier(
          n_trees=params["n_trees"],
          n_selected=params["n_selected"],
          n_layers=params["n_layers"],
          mask_type=params["mask_type"],
      )
      base_model.fit(X=X_train, y=y_train, X_val=X_test, y_val=y_test)

      y_pred = base_model.predict(X_test)
      mcc = matthews_corrcoef(y_test, y_pred)

      # Return the accuracy
      return mcc

  return objective

In [6]:
def train_with_best_hyperparameters(datasets, key):
  print("Currently training NCART model with dataset key:", key)

  # Create a Pandas DataFrame to store all experiment results
  results_df = pd.DataFrame(columns=['Fold', 'Accuracy', 'MCC'])

  # Perform 10-fold cross validation
  dataset_list = datasets[key]

  # Use the first data as the test for the HPO
  X_train, X_test, y_train, y_test = prepare_train_test_dataset(dataset_list, 0)

  objective_function = create_objective_for_ncart(X_train, X_test, y_train, y_test)

  study = optuna.create_study(direction='maximize')
  study.optimize(objective_function, n_trials=15, gc_after_trial=True)

  best_params = study.best_params
  print("Best hyperparameters:", best_params)

  # Use best hyperparams to conduct a 10-fold cross validation
  for i in range(10):
    X_train, X_test, y_train, y_test = prepare_train_test_dataset(dataset_list, i)

    # Train the model
    model = NCARClassifier(
        n_trees=best_params["n_trees"],
        n_selected=best_params["n_selected"],
        n_layers=best_params["n_layers"],
        mask_type=best_params["mask_type"],
    )
    model.fit(X=X_train, y=y_train, X_val=X_test, y_val=y_test)

    # Evaluate the model
    y_pred = model.predict(X_test)
    accuracy = accuracy_score(y_test, y_pred)
    mcc = matthews_corrcoef(y_test, y_pred)

    print("Fold", i+1, "Accuracy:", accuracy, "MCC:", mcc)
    results_df.loc[i] = [i+1, accuracy, mcc]

  return results_df

In [7]:
# Load the validation datasets

datasets = {}

# All

XII_all_nopcc_1 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/nopcc/fold_1.csv')
XII_all_nopcc_2 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/nopcc/fold_2.csv')
XII_all_nopcc_3 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/nopcc/fold_3.csv')
XII_all_nopcc_4 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/nopcc/fold_4.csv')
XII_all_nopcc_5 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/nopcc/fold_5.csv')
XII_all_nopcc_6 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/nopcc/fold_6.csv')
XII_all_nopcc_7 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/nopcc/fold_7.csv')
XII_all_nopcc_8 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/nopcc/fold_8.csv')
XII_all_nopcc_9 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/nopcc/fold_9.csv')
XII_all_nopcc_10 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/nopcc/fold_10.csv')
datasets['XII_all_nopcc'] = [XII_all_nopcc_1, XII_all_nopcc_2, XII_all_nopcc_3, XII_all_nopcc_4, XII_all_nopcc_5,
                                       XII_all_nopcc_6, XII_all_nopcc_7, XII_all_nopcc_8, XII_all_nopcc_9, XII_all_nopcc_10]

XII_all_pcc95_1 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/pcc95/fold_1.csv')
XII_all_pcc95_2 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/pcc95/fold_2.csv')
XII_all_pcc95_3 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/pcc95/fold_3.csv')
XII_all_pcc95_4 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/pcc95/fold_4.csv')
XII_all_pcc95_5 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/pcc95/fold_5.csv')
XII_all_pcc95_6 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/pcc95/fold_6.csv')
XII_all_pcc95_7 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/pcc95/fold_7.csv')
XII_all_pcc95_8 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/pcc95/fold_8.csv')
XII_all_pcc95_9 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/pcc95/fold_9.csv')
XII_all_pcc95_10 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/pcc95/fold_10.csv')
datasets['XII_all_pcc95'] = [XII_all_pcc95_1, XII_all_pcc95_2, XII_all_pcc95_3, XII_all_pcc95_4, XII_all_pcc95_5,
                                       XII_all_pcc95_6, XII_all_pcc95_7, XII_all_pcc95_8, XII_all_pcc95_9, XII_all_pcc95_10]

XII_all_pcc75_1 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/pcc75/fold_1.csv')
XII_all_pcc75_2 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/pcc75/fold_2.csv')
XII_all_pcc75_3 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/pcc75/fold_3.csv')
XII_all_pcc75_4 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/pcc75/fold_4.csv')
XII_all_pcc75_5 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/pcc75/fold_5.csv')
XII_all_pcc75_6 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/pcc75/fold_6.csv')
XII_all_pcc75_7 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/pcc75/fold_7.csv')
XII_all_pcc75_8 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/pcc75/fold_8.csv')
XII_all_pcc75_9 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/pcc75/fold_9.csv')
XII_all_pcc75_10 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/all/cv/pcc75/fold_10.csv')
datasets['XII_all_pcc75'] = [XII_all_pcc75_1, XII_all_pcc75_2, XII_all_pcc75_3, XII_all_pcc75_4, XII_all_pcc75_5,
                                       XII_all_pcc75_6, XII_all_pcc75_7, XII_all_pcc75_8, XII_all_pcc75_9, XII_all_pcc75_10]

# 200

XII_200_nopcc_1 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/nopcc/fold_1.csv')
XII_200_nopcc_2 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/nopcc/fold_2.csv')
XII_200_nopcc_3 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/nopcc/fold_3.csv')
XII_200_nopcc_4 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/nopcc/fold_4.csv')
XII_200_nopcc_5 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/nopcc/fold_5.csv')
XII_200_nopcc_6 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/nopcc/fold_6.csv')
XII_200_nopcc_7 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/nopcc/fold_7.csv')
XII_200_nopcc_8 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/nopcc/fold_8.csv')
XII_200_nopcc_9 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/nopcc/fold_9.csv')
XII_200_nopcc_10 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/nopcc/fold_10.csv')
datasets['XII_200_nopcc'] = [XII_200_nopcc_1, XII_200_nopcc_2, XII_200_nopcc_3, XII_200_nopcc_4, XII_200_nopcc_5,
                                       XII_200_nopcc_6, XII_200_nopcc_7, XII_200_nopcc_8, XII_200_nopcc_9, XII_200_nopcc_10]

XII_200_pcc95_1 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/pcc95/fold_1.csv')
XII_200_pcc95_2 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/pcc95/fold_2.csv')
XII_200_pcc95_3 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/pcc95/fold_3.csv')
XII_200_pcc95_4 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/pcc95/fold_4.csv')
XII_200_pcc95_5 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/pcc95/fold_5.csv')
XII_200_pcc95_6 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/pcc95/fold_6.csv')
XII_200_pcc95_7 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/pcc95/fold_7.csv')
XII_200_pcc95_8 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/pcc95/fold_8.csv')
XII_200_pcc95_9 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/pcc95/fold_9.csv')
XII_200_pcc95_10 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/pcc95/fold_10.csv')
datasets['XII_200_pcc95'] = [XII_200_pcc95_1, XII_200_pcc95_2, XII_200_pcc95_3, XII_200_pcc95_4, XII_200_pcc95_5,
                                       XII_200_pcc95_6, XII_200_pcc95_7, XII_200_pcc95_8, XII_200_pcc95_9, XII_200_pcc95_10]

XII_200_pcc75_1 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/pcc75/fold_1.csv')
XII_200_pcc75_2 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/pcc75/fold_2.csv')
XII_200_pcc75_3 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/pcc75/fold_3.csv')
XII_200_pcc75_4 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/pcc75/fold_4.csv')
XII_200_pcc75_5 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/pcc75/fold_5.csv')
XII_200_pcc75_6 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/pcc75/fold_6.csv')
XII_200_pcc75_7 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/pcc75/fold_7.csv')
XII_200_pcc75_8 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/pcc75/fold_8.csv')
XII_200_pcc75_9 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/pcc75/fold_9.csv')
XII_200_pcc75_10 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/200/cv/pcc75/fold_10.csv')
datasets['XII_200_pcc75'] = [XII_200_pcc75_1, XII_200_pcc75_2, XII_200_pcc75_3, XII_200_pcc75_4, XII_200_pcc75_5,
                                       XII_200_pcc75_6, XII_200_pcc75_7, XII_200_pcc75_8, XII_200_pcc75_9, XII_200_pcc75_10]

# 150

XII_150_nopcc_1 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/nopcc/fold_1.csv')
XII_150_nopcc_2 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/nopcc/fold_2.csv')
XII_150_nopcc_3 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/nopcc/fold_3.csv')
XII_150_nopcc_4 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/nopcc/fold_4.csv')
XII_150_nopcc_5 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/nopcc/fold_5.csv')
XII_150_nopcc_6 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/nopcc/fold_6.csv')
XII_150_nopcc_7 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/nopcc/fold_7.csv')
XII_150_nopcc_8 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/nopcc/fold_8.csv')
XII_150_nopcc_9 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/nopcc/fold_9.csv')
XII_150_nopcc_10 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/nopcc/fold_10.csv')
datasets['XII_150_nopcc'] = [XII_150_nopcc_1, XII_150_nopcc_2, XII_150_nopcc_3, XII_150_nopcc_4, XII_150_nopcc_5,
                                       XII_150_nopcc_6, XII_150_nopcc_7, XII_150_nopcc_8, XII_150_nopcc_9, XII_150_nopcc_10]

XII_150_pcc95_1 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/pcc95/fold_1.csv')
XII_150_pcc95_2 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/pcc95/fold_2.csv')
XII_150_pcc95_3 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/pcc95/fold_3.csv')
XII_150_pcc95_4 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/pcc95/fold_4.csv')
XII_150_pcc95_5 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/pcc95/fold_5.csv')
XII_150_pcc95_6 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/pcc95/fold_6.csv')
XII_150_pcc95_7 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/pcc95/fold_7.csv')
XII_150_pcc95_8 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/pcc95/fold_8.csv')
XII_150_pcc95_9 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/pcc95/fold_9.csv')
XII_150_pcc95_10 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/pcc95/fold_10.csv')
datasets['XII_150_pcc95'] = [XII_150_pcc95_1, XII_150_pcc95_2, XII_150_pcc95_3, XII_150_pcc95_4, XII_150_pcc95_5,
                                       XII_150_pcc95_6, XII_150_pcc95_7, XII_150_pcc95_8, XII_150_pcc95_9, XII_150_pcc95_10]

XII_150_pcc75_1 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/pcc75/fold_1.csv')
XII_150_pcc75_2 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/pcc75/fold_2.csv')
XII_150_pcc75_3 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/pcc75/fold_3.csv')
XII_150_pcc75_4 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/pcc75/fold_4.csv')
XII_150_pcc75_5 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/pcc75/fold_5.csv')
XII_150_pcc75_6 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/pcc75/fold_6.csv')
XII_150_pcc75_7 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/pcc75/fold_7.csv')
XII_150_pcc75_8 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/pcc75/fold_8.csv')
XII_150_pcc75_9 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/pcc75/fold_9.csv')
XII_150_pcc75_10 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/150/cv/pcc75/fold_10.csv')
datasets['XII_150_pcc75'] = [XII_150_pcc75_1, XII_150_pcc75_2, XII_150_pcc75_3, XII_150_pcc75_4, XII_150_pcc75_5,
                                       XII_150_pcc75_6, XII_150_pcc75_7, XII_150_pcc75_8, XII_150_pcc75_9, XII_150_pcc75_10]

# 100

XII_100_nopcc_1 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/nopcc/fold_1.csv')
XII_100_nopcc_2 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/nopcc/fold_2.csv')
XII_100_nopcc_3 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/nopcc/fold_3.csv')
XII_100_nopcc_4 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/nopcc/fold_4.csv')
XII_100_nopcc_5 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/nopcc/fold_5.csv')
XII_100_nopcc_6 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/nopcc/fold_6.csv')
XII_100_nopcc_7 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/nopcc/fold_7.csv')
XII_100_nopcc_8 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/nopcc/fold_8.csv')
XII_100_nopcc_9 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/nopcc/fold_9.csv')
XII_100_nopcc_10 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/nopcc/fold_10.csv')
datasets['XII_100_nopcc'] = [XII_100_nopcc_1, XII_100_nopcc_2, XII_100_nopcc_3, XII_100_nopcc_4, XII_100_nopcc_5,
                                       XII_100_nopcc_6, XII_100_nopcc_7, XII_100_nopcc_8, XII_100_nopcc_9, XII_100_nopcc_10]

XII_100_pcc95_1 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/pcc95/fold_1.csv')
XII_100_pcc95_2 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/pcc95/fold_2.csv')
XII_100_pcc95_3 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/pcc95/fold_3.csv')
XII_100_pcc95_4 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/pcc95/fold_4.csv')
XII_100_pcc95_5 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/pcc95/fold_5.csv')
XII_100_pcc95_6 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/pcc95/fold_6.csv')
XII_100_pcc95_7 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/pcc95/fold_7.csv')
XII_100_pcc95_8 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/pcc95/fold_8.csv')
XII_100_pcc95_9 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/pcc95/fold_9.csv')
XII_100_pcc95_10 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/pcc95/fold_10.csv')
datasets['XII_100_pcc95'] = [XII_100_pcc95_1, XII_100_pcc95_2, XII_100_pcc95_3, XII_100_pcc95_4, XII_100_pcc95_5,
                                       XII_100_pcc95_6, XII_100_pcc95_7, XII_100_pcc95_8, XII_100_pcc95_9, XII_100_pcc95_10]

XII_100_pcc75_1 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/pcc75/fold_1.csv')
XII_100_pcc75_2 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/pcc75/fold_2.csv')
XII_100_pcc75_3 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/pcc75/fold_3.csv')
XII_100_pcc75_4 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/pcc75/fold_4.csv')
XII_100_pcc75_5 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/pcc75/fold_5.csv')
XII_100_pcc75_6 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/pcc75/fold_6.csv')
XII_100_pcc75_7 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/pcc75/fold_7.csv')
XII_100_pcc75_8 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/pcc75/fold_8.csv')
XII_100_pcc75_9 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/pcc75/fold_9.csv')
XII_100_pcc75_10 = pd.read_csv('/content/drive/MyDrive/OrderedDataset/XII/100/cv/pcc75/fold_10.csv')
datasets['XII_100_pcc75'] = [XII_100_pcc75_1, XII_100_pcc75_2, XII_100_pcc75_3, XII_100_pcc75_4, XII_100_pcc75_5,
                                       XII_100_pcc75_6, XII_100_pcc75_7, XII_100_pcc75_8, XII_100_pcc75_9, XII_100_pcc75_10]

In [8]:
def view_results_df(results_df, key):
    print("10-fold cross validation results for results_df with key:", key)
    for i in range(len(results_df)):
        # Format accuracy and MCC to 3 decimal places
        accuracy = f"{results_df['Accuracy'][i]:.3f}"
        mcc = f"{results_df['MCC'][i]:.3f}"
        print(f"Fold {i}, Accuracy: {accuracy}, MCC: {mcc}")


In [9]:
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)

In [10]:
import time
start_time = time.time()
XII_all_nopcc_results_df = train_with_base_ncart(datasets, 'XII_all_nopcc')
elapsed_time = time.time() - start_time
print(f"Elapsed time: {elapsed_time:.2f} seconds")
print("\n---------------------------------------------------------------------\n")

Currently training NCART model with dataset key: XII_all_nopcc
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.736240 |  Val Loss 0.726084
Epoch 1: Train Loss 0.718239 |  Val Loss 0.716286
Epoch 2: Train Loss 0.702628 |  Val Loss 0.709200
Epoch 3: Train Loss 0.689213 |  Val Loss 0.700137
Epoch 4: Train Loss 0.677563 |  Val Loss 0.692503
Epoch 5: Train Loss 0.665874 |  Val Loss 0.683481
Epoch 6: Train Loss 0.654924 |  Val Loss 0.674398
Epoch 7: Train Loss 0.644565 |  Val Loss 0.665678
Epoch 8: Train Loss 0.634816 |  Val Loss 0.659401
Epoch 9: Train Loss 0.625569 |  Val Loss 0.653357
Epoch 10: Train Loss 0.616742 |  Val Loss 0.647669
Epoch 11: Train Loss 0.607988 |  Val Loss 0.642591
Epoch 12: Train Loss 0.599524 |  Val Loss 0.637664
Epoch 13: Train Loss 0.591397 |  Val Loss 0.631906
Epoch 14: Train Loss 0.583394 |  Val Loss 0.627345
Epoch 15: Train Loss 0.575538 |  Val Loss 0.623182
Epoch 16: Train Loss 0.567868 |  Val Loss 0.617877
Epoch 17: Train Loss 0.560368 |  Val Lo

In [11]:
start_time = time.time()
XII_all_pcc95_results_df = train_with_base_ncart(datasets, 'XII_all_pcc95')
elapsed_time = time.time() - start_time
print(f"Elapsed time: {elapsed_time:.2f} seconds")
print("\n---------------------------------------------------------------------\n")

Currently training NCART model with dataset key: XII_all_pcc95
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.707741 |  Val Loss 0.708880
Epoch 1: Train Loss 0.701938 |  Val Loss 0.707046
Epoch 2: Train Loss 0.696487 |  Val Loss 0.704123
Epoch 3: Train Loss 0.691370 |  Val Loss 0.701100
Epoch 4: Train Loss 0.686492 |  Val Loss 0.698878
Epoch 5: Train Loss 0.682120 |  Val Loss 0.696602
Epoch 6: Train Loss 0.678184 |  Val Loss 0.694857
Epoch 7: Train Loss 0.674358 |  Val Loss 0.693101
Epoch 8: Train Loss 0.670635 |  Val Loss 0.691312
Epoch 9: Train Loss 0.666824 |  Val Loss 0.689601
Epoch 10: Train Loss 0.663093 |  Val Loss 0.687735
Epoch 11: Train Loss 0.659354 |  Val Loss 0.685608
Epoch 12: Train Loss 0.655592 |  Val Loss 0.683700
Epoch 13: Train Loss 0.651917 |  Val Loss 0.681542
Epoch 14: Train Loss 0.648262 |  Val Loss 0.679176
Epoch 15: Train Loss 0.644600 |  Val Loss 0.676709
Epoch 16: Train Loss 0.640990 |  Val Loss 0.674175
Epoch 17: Train Loss 0.637264 |  Val Lo

In [12]:
start_time = time.time()
XII_all_pcc75_results_df = train_with_base_ncart(datasets, 'XII_all_pcc75')
elapsed_time = time.time() - start_time
print(f"Elapsed time: {elapsed_time:.2f} seconds")
print("\n---------------------------------------------------------------------\n")

Currently training NCART model with dataset key: XII_all_pcc75
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.747616 |  Val Loss 0.739716
Epoch 1: Train Loss 0.740321 |  Val Loss 0.732076
Epoch 2: Train Loss 0.733543 |  Val Loss 0.727032
Epoch 3: Train Loss 0.726873 |  Val Loss 0.723126
Epoch 4: Train Loss 0.720825 |  Val Loss 0.719322
Epoch 5: Train Loss 0.715137 |  Val Loss 0.715629
Epoch 6: Train Loss 0.709947 |  Val Loss 0.711222
Epoch 7: Train Loss 0.704755 |  Val Loss 0.706313
Epoch 8: Train Loss 0.699666 |  Val Loss 0.701213
Epoch 9: Train Loss 0.694823 |  Val Loss 0.696231
Epoch 10: Train Loss 0.690091 |  Val Loss 0.691736
Epoch 11: Train Loss 0.685490 |  Val Loss 0.687675
Epoch 12: Train Loss 0.680997 |  Val Loss 0.683654
Epoch 13: Train Loss 0.676656 |  Val Loss 0.679686
Epoch 14: Train Loss 0.672416 |  Val Loss 0.675825
Epoch 15: Train Loss 0.668285 |  Val Loss 0.672012
Epoch 16: Train Loss 0.664184 |  Val Loss 0.668311
Epoch 17: Train Loss 0.660141 |  Val Lo

In [13]:
start_time = time.time()
XII_200_nopcc_results_df = train_with_base_ncart(datasets, 'XII_200_nopcc')
elapsed_time = time.time() - start_time
print(f"Elapsed time: {elapsed_time:.2f} seconds")

Currently training NCART model with dataset key: XII_200_nopcc
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.738912 |  Val Loss 0.713524
Epoch 1: Train Loss 0.716871 |  Val Loss 0.699731
Epoch 2: Train Loss 0.699037 |  Val Loss 0.688693
Epoch 3: Train Loss 0.683430 |  Val Loss 0.675066
Epoch 4: Train Loss 0.669890 |  Val Loss 0.666601
Epoch 5: Train Loss 0.656824 |  Val Loss 0.659945
Epoch 6: Train Loss 0.645503 |  Val Loss 0.651990
Epoch 7: Train Loss 0.634882 |  Val Loss 0.644847
Epoch 8: Train Loss 0.624392 |  Val Loss 0.638147
Epoch 9: Train Loss 0.614109 |  Val Loss 0.632244
Epoch 10: Train Loss 0.604299 |  Val Loss 0.625977
Epoch 11: Train Loss 0.594866 |  Val Loss 0.620671
Epoch 12: Train Loss 0.585714 |  Val Loss 0.615189
Epoch 13: Train Loss 0.576740 |  Val Loss 0.609196
Epoch 14: Train Loss 0.567903 |  Val Loss 0.603445
Epoch 15: Train Loss 0.559278 |  Val Loss 0.597414
Epoch 16: Train Loss 0.550897 |  Val Loss 0.592005
Epoch 17: Train Loss 0.542690 |  Val Lo

In [14]:
start_time = time.time()
XII_200_pcc95_results_df = train_with_base_ncart(datasets, 'XII_200_pcc95')
elapsed_time = time.time() - start_time
print(f"Elapsed time: {elapsed_time:.2f} seconds")

Currently training NCART model with dataset key: XII_200_pcc95
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.707232 |  Val Loss 0.706583
Epoch 1: Train Loss 0.700550 |  Val Loss 0.702554
Epoch 2: Train Loss 0.694153 |  Val Loss 0.698168
Epoch 3: Train Loss 0.688601 |  Val Loss 0.695174
Epoch 4: Train Loss 0.683391 |  Val Loss 0.692135
Epoch 5: Train Loss 0.678732 |  Val Loss 0.688856
Epoch 6: Train Loss 0.674396 |  Val Loss 0.685791
Epoch 7: Train Loss 0.670324 |  Val Loss 0.682331
Epoch 8: Train Loss 0.666272 |  Val Loss 0.679478
Epoch 9: Train Loss 0.662122 |  Val Loss 0.676506
Epoch 10: Train Loss 0.657878 |  Val Loss 0.673671
Epoch 11: Train Loss 0.653677 |  Val Loss 0.671206
Epoch 12: Train Loss 0.649458 |  Val Loss 0.668752
Epoch 13: Train Loss 0.645339 |  Val Loss 0.665956
Epoch 14: Train Loss 0.641204 |  Val Loss 0.662808
Epoch 15: Train Loss 0.636975 |  Val Loss 0.659696
Epoch 16: Train Loss 0.632748 |  Val Loss 0.657279
Epoch 17: Train Loss 0.628578 |  Val Lo

In [15]:
start_time = time.time()
XII_200_pcc75_results_df = train_with_base_ncart(datasets, 'XII_200_pcc75')
elapsed_time = time.time() - start_time
print(f"Elapsed time: {elapsed_time:.2f} seconds")

Currently training NCART model with dataset key: XII_200_pcc75
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.744272 |  Val Loss 0.745057
Epoch 1: Train Loss 0.736158 |  Val Loss 0.739884
Epoch 2: Train Loss 0.729358 |  Val Loss 0.735939
Epoch 3: Train Loss 0.722678 |  Val Loss 0.732543
Epoch 4: Train Loss 0.716309 |  Val Loss 0.728080
Epoch 5: Train Loss 0.710160 |  Val Loss 0.724383
Epoch 6: Train Loss 0.704570 |  Val Loss 0.721540
Epoch 7: Train Loss 0.698922 |  Val Loss 0.718358
Epoch 8: Train Loss 0.693532 |  Val Loss 0.714704
Epoch 9: Train Loss 0.688189 |  Val Loss 0.711337
Epoch 10: Train Loss 0.682920 |  Val Loss 0.707825
Epoch 11: Train Loss 0.677867 |  Val Loss 0.704052
Epoch 12: Train Loss 0.672844 |  Val Loss 0.700632
Epoch 13: Train Loss 0.667902 |  Val Loss 0.697475
Epoch 14: Train Loss 0.663133 |  Val Loss 0.694806
Epoch 15: Train Loss 0.658496 |  Val Loss 0.691711
Epoch 16: Train Loss 0.654004 |  Val Loss 0.689586
Epoch 17: Train Loss 0.649644 |  Val Lo

In [16]:
start_time = time.time()
XII_150_nopcc_results_df = train_with_base_ncart(datasets, 'XII_150_nopcc')
elapsed_time = time.time() - start_time
print(f"Elapsed time: {elapsed_time:.2f} seconds")

Currently training NCART model with dataset key: XII_150_nopcc
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.735571 |  Val Loss 0.714424
Epoch 1: Train Loss 0.711397 |  Val Loss 0.699174
Epoch 2: Train Loss 0.692724 |  Val Loss 0.682838
Epoch 3: Train Loss 0.676410 |  Val Loss 0.668175
Epoch 4: Train Loss 0.662028 |  Val Loss 0.653312
Epoch 5: Train Loss 0.647887 |  Val Loss 0.638955
Epoch 6: Train Loss 0.635017 |  Val Loss 0.626988
Epoch 7: Train Loss 0.623367 |  Val Loss 0.615788
Epoch 8: Train Loss 0.611878 |  Val Loss 0.606265
Epoch 9: Train Loss 0.600651 |  Val Loss 0.596905
Epoch 10: Train Loss 0.590032 |  Val Loss 0.590510
Epoch 11: Train Loss 0.579655 |  Val Loss 0.583027
Epoch 12: Train Loss 0.569671 |  Val Loss 0.575960
Epoch 13: Train Loss 0.559908 |  Val Loss 0.569682
Epoch 14: Train Loss 0.550094 |  Val Loss 0.563610
Epoch 15: Train Loss 0.540646 |  Val Loss 0.555998
Epoch 16: Train Loss 0.531502 |  Val Loss 0.550083
Epoch 17: Train Loss 0.522830 |  Val Lo

In [17]:
start_time = time.time()
XII_150_pcc95_results_df = train_with_base_ncart(datasets, 'XII_150_pcc95')
elapsed_time = time.time() - start_time
print(f"Elapsed time: {elapsed_time:.2f} seconds")

Currently training NCART model with dataset key: XII_150_pcc95
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.707957 |  Val Loss 0.701494
Epoch 1: Train Loss 0.700287 |  Val Loss 0.694372
Epoch 2: Train Loss 0.693229 |  Val Loss 0.688249
Epoch 3: Train Loss 0.687095 |  Val Loss 0.682561
Epoch 4: Train Loss 0.681463 |  Val Loss 0.676474
Epoch 5: Train Loss 0.676135 |  Val Loss 0.671770
Epoch 6: Train Loss 0.671056 |  Val Loss 0.667239
Epoch 7: Train Loss 0.666484 |  Val Loss 0.663186
Epoch 8: Train Loss 0.661963 |  Val Loss 0.659399
Epoch 9: Train Loss 0.657613 |  Val Loss 0.655590
Epoch 10: Train Loss 0.653169 |  Val Loss 0.651793
Epoch 11: Train Loss 0.648696 |  Val Loss 0.647838
Epoch 12: Train Loss 0.644395 |  Val Loss 0.643970
Epoch 13: Train Loss 0.639964 |  Val Loss 0.640423
Epoch 14: Train Loss 0.635534 |  Val Loss 0.636848
Epoch 15: Train Loss 0.631142 |  Val Loss 0.633130
Epoch 16: Train Loss 0.626775 |  Val Loss 0.629297
Epoch 17: Train Loss 0.622442 |  Val Lo

In [18]:
start_time = time.time()
XII_150_pcc75_results_df = train_with_base_ncart(datasets, 'XII_150_pcc75')
elapsed_time = time.time() - start_time
print(f"Elapsed time: {elapsed_time:.2f} seconds")

Currently training NCART model with dataset key: XII_150_pcc75
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.744573 |  Val Loss 0.745484
Epoch 1: Train Loss 0.736834 |  Val Loss 0.740066
Epoch 2: Train Loss 0.729659 |  Val Loss 0.734638
Epoch 3: Train Loss 0.722999 |  Val Loss 0.729355
Epoch 4: Train Loss 0.716554 |  Val Loss 0.723925
Epoch 5: Train Loss 0.710349 |  Val Loss 0.718711
Epoch 6: Train Loss 0.704539 |  Val Loss 0.713549
Epoch 7: Train Loss 0.698999 |  Val Loss 0.709527
Epoch 8: Train Loss 0.693508 |  Val Loss 0.705243
Epoch 9: Train Loss 0.688342 |  Val Loss 0.700462
Epoch 10: Train Loss 0.683099 |  Val Loss 0.695861
Epoch 11: Train Loss 0.678127 |  Val Loss 0.690499
Epoch 12: Train Loss 0.673265 |  Val Loss 0.684888
Epoch 13: Train Loss 0.668481 |  Val Loss 0.680139
Epoch 14: Train Loss 0.663748 |  Val Loss 0.675570
Epoch 15: Train Loss 0.659312 |  Val Loss 0.671191
Epoch 16: Train Loss 0.654959 |  Val Loss 0.666686
Epoch 17: Train Loss 0.650501 |  Val Lo

In [19]:
start_time = time.time()
XII_100_nopcc_results_df = train_with_base_ncart(datasets, 'XII_100_nopcc')
elapsed_time = time.time() - start_time
print(f"Elapsed time: {elapsed_time:.2f} seconds")

Streaming output truncated to the last 5000 lines.
Epoch 214: Train Loss 0.034943 |  Val Loss 0.049919
Epoch 215: Train Loss 0.034604 |  Val Loss 0.049561
Epoch 216: Train Loss 0.034268 |  Val Loss 0.049149
Epoch 217: Train Loss 0.033938 |  Val Loss 0.048702
Epoch 218: Train Loss 0.033612 |  Val Loss 0.048316
Epoch 219: Train Loss 0.033290 |  Val Loss 0.047934
Epoch 220: Train Loss 0.032973 |  Val Loss 0.047537
Epoch 221: Train Loss 0.032659 |  Val Loss 0.047168
Epoch 222: Train Loss 0.032350 |  Val Loss 0.046865
Epoch 223: Train Loss 0.032046 |  Val Loss 0.046500
Epoch 224: Train Loss 0.031745 |  Val Loss 0.046086
Epoch 225: Train Loss 0.031449 |  Val Loss 0.045740
Epoch 226: Train Loss 0.031155 |  Val Loss 0.045370
Epoch 227: Train Loss 0.030866 |  Val Loss 0.045002
Epoch 228: Train Loss 0.030580 |  Val Loss 0.044669
Epoch 229: Train Loss 0.030299 |  Val Loss 0.044388
Epoch 230: Train Loss 0.030021 |  Val Loss 0.044043
Epoch 231: Train Loss 0.029747 |  Val Loss 0.043643
Epoch 232: Tr

In [20]:
start_time = time.time()
XII_100_pcc95_results_df = train_with_base_ncart(datasets, 'XII_100_pcc95')
elapsed_time = time.time() - start_time
print(f"Elapsed time: {elapsed_time:.2f} seconds")

Currently training NCART model with dataset key: XII_100_pcc95
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.752110 |  Val Loss 0.725305
Epoch 1: Train Loss 0.731547 |  Val Loss 0.715936
Epoch 2: Train Loss 0.713288 |  Val Loss 0.704104
Epoch 3: Train Loss 0.697713 |  Val Loss 0.690641
Epoch 4: Train Loss 0.683571 |  Val Loss 0.677956
Epoch 5: Train Loss 0.670826 |  Val Loss 0.665193
Epoch 6: Train Loss 0.659297 |  Val Loss 0.652783
Epoch 7: Train Loss 0.648127 |  Val Loss 0.641675
Epoch 8: Train Loss 0.637168 |  Val Loss 0.631498
Epoch 9: Train Loss 0.626743 |  Val Loss 0.622093
Epoch 10: Train Loss 0.616753 |  Val Loss 0.613187
Epoch 11: Train Loss 0.607209 |  Val Loss 0.604196
Epoch 12: Train Loss 0.597949 |  Val Loss 0.594549
Epoch 13: Train Loss 0.589292 |  Val Loss 0.584756
Epoch 14: Train Loss 0.580957 |  Val Loss 0.576201
Epoch 15: Train Loss 0.572906 |  Val Loss 0.567597
Epoch 16: Train Loss 0.565045 |  Val Loss 0.559317
Epoch 17: Train Loss 0.557447 |  Val Lo

In [21]:
start_time = time.time()
XII_100_pcc75_results_df = train_with_base_ncart(datasets, 'XII_100_pcc75')
elapsed_time = time.time() - start_time
print(f"Elapsed time: {elapsed_time:.2f} seconds")

Currently training NCART model with dataset key: XII_100_pcc75
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.719223 |  Val Loss 0.700825
Epoch 1: Train Loss 0.710218 |  Val Loss 0.692572
Epoch 2: Train Loss 0.702241 |  Val Loss 0.682358
Epoch 3: Train Loss 0.694143 |  Val Loss 0.670965
Epoch 4: Train Loss 0.686924 |  Val Loss 0.665552
Epoch 5: Train Loss 0.680559 |  Val Loss 0.660859
Epoch 6: Train Loss 0.674343 |  Val Loss 0.656526
Epoch 7: Train Loss 0.668624 |  Val Loss 0.652019
Epoch 8: Train Loss 0.663316 |  Val Loss 0.648946
Epoch 9: Train Loss 0.658482 |  Val Loss 0.645608
Epoch 10: Train Loss 0.654022 |  Val Loss 0.642107
Epoch 11: Train Loss 0.649889 |  Val Loss 0.638389
Epoch 12: Train Loss 0.645976 |  Val Loss 0.634942
Epoch 13: Train Loss 0.642137 |  Val Loss 0.635499
Epoch 14: Train Loss 0.638369 |  Val Loss 0.632710
Epoch 15: Train Loss 0.634686 |  Val Loss 0.630754
Epoch 16: Train Loss 0.631114 |  Val Loss 0.628696
Epoch 17: Train Loss 0.627584 |  Val Lo

In [22]:
print("Base Model:")
print('\n---------------------------------------------------------------------\n')
view_results_df(XII_all_nopcc_results_df, 'XII_all_nopcc')
print('\n---------------------------------------------------------------------\n')
view_results_df(XII_all_pcc95_results_df, 'XII_all_pcc95')
print('\n---------------------------------------------------------------------\n')
view_results_df(XII_all_nopcc_results_df, 'XII_all_pcc75')
print('\n---------------------------------------------------------------------\n')
view_results_df(XII_200_nopcc_results_df, 'XII_200_nopcc')
print('\n---------------------------------------------------------------------\n')
view_results_df(XII_200_pcc95_results_df, 'XII_200_pcc95')
print('\n---------------------------------------------------------------------\n')
view_results_df(XII_200_nopcc_results_df, 'XII_200_pcc75')
print('\n---------------------------------------------------------------------\n')
view_results_df(XII_150_nopcc_results_df, 'XII_150_nopcc')
print('\n---------------------------------------------------------------------\n')
view_results_df(XII_150_pcc95_results_df, 'XII_150_pcc95')
print('\n---------------------------------------------------------------------\n')
view_results_df(XII_150_nopcc_results_df, 'XII_150_pcc75')
print('\n---------------------------------------------------------------------\n')
view_results_df(XII_100_nopcc_results_df, 'XII_100_nopcc')
print('\n---------------------------------------------------------------------\n')
view_results_df(XII_100_pcc95_results_df, 'XII_100_pcc95')
print('\n---------------------------------------------------------------------\n')
view_results_df(XII_100_nopcc_results_df, 'XII_100_pcc75')
print('\n---------------------------------------------------------------------\n')


Base Model:

---------------------------------------------------------------------

10-fold cross validation results for results_df with key: XII_all_nopcc
Fold 0, Accuracy: 0.796, MCC: 0.592
Fold 1, Accuracy: 0.898, MCC: 0.797
Fold 2, Accuracy: 0.939, MCC: 0.878
Fold 3, Accuracy: 0.918, MCC: 0.837
Fold 4, Accuracy: 0.959, MCC: 0.918
Fold 5, Accuracy: 0.857, MCC: 0.715
Fold 6, Accuracy: 0.796, MCC: 0.594
Fold 7, Accuracy: 0.917, MCC: 0.833
Fold 8, Accuracy: 0.833, MCC: 0.689
Fold 9, Accuracy: 0.771, MCC: 0.546

---------------------------------------------------------------------

10-fold cross validation results for results_df with key: XII_all_pcc95
Fold 0, Accuracy: 0.857, MCC: 0.715
Fold 1, Accuracy: 0.898, MCC: 0.797
Fold 2, Accuracy: 0.898, MCC: 0.802
Fold 3, Accuracy: 0.878, MCC: 0.755
Fold 4, Accuracy: 0.939, MCC: 0.878
Fold 5, Accuracy: 0.878, MCC: 0.758
Fold 6, Accuracy: 0.857, MCC: 0.715
Fold 7, Accuracy: 0.979, MCC: 0.959
Fold 8, Accuracy: 0.833, MCC: 0.669
Fold 9, Accuracy

In [23]:
start_time = time.time()
XII_all_nopcc_results_df = train_with_best_hyperparameters(datasets, 'XII_all_nopcc')
elapsed_time = time.time() - start_time
print(f"Elapsed time: {elapsed_time:.2f} seconds")

[I 2025-01-04 15:54:21,283] A new study created in memory with name: no-name-30abae89-bfb9-450e-9e49-0e6d8fb6a12f


Currently training NCART model with dataset key: XII_all_nopcc
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.694185 |  Val Loss 0.700982
Epoch 1: Train Loss 0.693840 |  Val Loss 0.700586
Epoch 2: Train Loss 0.693520 |  Val Loss 0.700224
Epoch 3: Train Loss 0.693230 |  Val Loss 0.699887
Epoch 4: Train Loss 0.692964 |  Val Loss 0.699577
Epoch 5: Train Loss 0.692723 |  Val Loss 0.699293
Epoch 6: Train Loss 0.692504 |  Val Loss 0.699034
Epoch 7: Train Loss 0.692308 |  Val Loss 0.698800
Epoch 8: Train Loss 0.692133 |  Val Loss 0.698592
Epoch 9: Train Loss 0.691977 |  Val Loss 0.698407
Epoch 10: Train Loss 0.691839 |  Val Loss 0.698243
Epoch 11: Train Loss 0.691716 |  Val Loss 0.698100
Epoch 12: Train Loss 0.691606 |  Val Loss 0.697975
Epoch 13: Train Loss 0.691507 |  Val Loss 0.697865
Epoch 14: Train Loss 0.691416 |  Val Loss 0.697769
Epoch 15: Train Loss 0.691330 |  Val Loss 0.697685
Epoch 16: Train Loss 0.691248 |  Val Loss 0.697610
Epoch 17: Train Loss 0.691167 |  Val Lo

[I 2025-01-04 15:54:29,849] Trial 0 finished with value: 0.3542918290328953 and parameters: {'n_trees': 8, 'n_selected': 4, 'n_layers': 1, 'mask_type': 'sparsemax'}. Best is trial 0 with value: 0.3542918290328953.


Epoch 839: Train Loss 0.466094 |  Val Loss 0.545568
Epoch 840: Train Loss 0.465942 |  Val Loss 0.545601
Epoch 841: Train Loss 0.465792 |  Val Loss 0.545661
Epoch 842: Train Loss 0.465640 |  Val Loss 0.545724
Epoch 843: Train Loss 0.465489 |  Val Loss 0.545753
Epoch 844: Train Loss 0.465339 |  Val Loss 0.545741
Epoch 845: Train Loss 0.465188 |  Val Loss 0.545695
Epoch 846: Train Loss 0.465038 |  Val Loss 0.545650
Epoch 847: Train Loss 0.464888 |  Val Loss 0.545621
Epoch 848: Train Loss 0.464737 |  Val Loss 0.545619
Epoch 849: Train Loss 0.464589 |  Val Loss 0.545618
Epoch 850: Train Loss 0.464440 |  Val Loss 0.545622
Validation loss has not improved for 10 steps!
Early stopping applies.
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.740406 |  Val Loss 0.716856
Epoch 1: Train Loss 0.710892 |  Val Loss 0.696231
Epoch 2: Train Loss 0.685386 |  Val Loss 0.679782
Epoch 3: Train Loss 0.663273 |  Val Loss 0.663876
Epoch 4: Train Loss 0.643262 |  Val Loss 0.649804
Epoch 5: Train

[I 2025-01-04 15:54:31,916] Trial 1 finished with value: 0.7963283217283071 and parameters: {'n_trees': 88, 'n_selected': 16, 'n_layers': 6, 'mask_type': 'entmax'}. Best is trial 1 with value: 0.7963283217283071.


...

Epoch 174: Train Loss 0.093092 |  Val Loss 0.367117
Epoch 175: Train Loss 0.091748 |  Val Loss 0.369696
Epoch 176: Train Loss 0.090634 |  Val Loss 0.365163
Epoch 177: Train Loss 0.089300 |  Val Loss 0.368646
Epoch 178: Train Loss 0.088166 |  Val Loss 0.367669
Epoch 179: Train Loss 0.086946 |  Val Loss 0.373430
Epoch 180: Train Loss 0.085829 |  Val Loss 0.369187
Epoch 181: Train Loss 0.084721 |  Val Loss 0.366378
Epoch 182: Train Loss 0.083600 |  Val Loss 0.372254
Epoch 183: Train Loss 0.082524 |  Val Loss 0.376709
Epoch 184: Train Loss 0.081454 |  Val Loss 0.366029
Epoch 185: Train Loss 0.080426 |  Val Loss 0.366602
Epoch 186: Train Loss 0.079342 |  Val Loss 0.373336
Epoch 187: Train Loss 0.078373 |  Val Loss 0.366465
Validation loss has not improved for 10 steps!
Early stopping applies.
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.688705 |  Val Loss 0.675065
Epoch 1: Train Loss 0.674880 |  Val Loss 0.667179
Epoch 2: Train Loss 0.664659 |  Val Loss 0.662284
Epoch 3: T

[I 2025-01-04 15:55:07,732] Trial 13 finished with value: 0.715 and parameters: {'n_trees': 104, 'n_selected': 24, 'n_layers': 2, 'mask_type': 'sparsemax'}. Best is trial 6 with value: 0.7966666666666666.


Epoch 105: Train Loss 0.097955 |  Val Loss 0.339561
Epoch 106: Train Loss 0.096598 |  Val Loss 0.342758
Epoch 107: Train Loss 0.094184 |  Val Loss 0.343536
Epoch 108: Train Loss 0.091537 |  Val Loss 0.344749
Epoch 109: Train Loss 0.088801 |  Val Loss 0.342091
Epoch 110: Train Loss 0.085946 |  Val Loss 0.338610
Epoch 111: Train Loss 0.084730 |  Val Loss 0.339065
Epoch 112: Train Loss 0.081466 |  Val Loss 0.342819
Epoch 113: Train Loss 0.079873 |  Val Loss 0.342940
Epoch 114: Train Loss 0.077906 |  Val Loss 0.343647
Epoch 115: Train Loss 0.075945 |  Val Loss 0.342190
Epoch 116: Train Loss 0.073757 |  Val Loss 0.340577
Epoch 117: Train Loss 0.072011 |  Val Loss 0.341220
Epoch 118: Train Loss 0.070635 |  Val Loss 0.339721
Epoch 119: Train Loss 0.068320 |  Val Loss 0.342396
Epoch 120: Train Loss 0.066864 |  Val Loss 0.341070
Epoch 121: Train Loss 0.065415 |  Val Loss 0.340381
Validation loss has not improved for 10 steps!
Early stopping applies.
On Device:  cuda:0
Binary classification
Epoc

[I 2025-01-04 15:55:09,981] Trial 14 finished with value: 0.7579309393388919 and parameters: {'n_trees': 64, 'n_selected': 12, 'n_layers': 4, 'mask_type': 'entmax'}. Best is trial 6 with value: 0.7966666666666666.


Streaming output truncated to the last 5000 lines.
Epoch 611: Train Loss 0.250516 |  Val Loss 0.291591
Epoch 612: Train Loss 0.250060 |  Val Loss 0.291236
Epoch 613: Train Loss 0.249605 |  Val Loss 0.290894
Epoch 614: Train Loss 0.249149 |  Val Loss 0.290559
Epoch 615: Train Loss 0.248696 |  Val Loss 0.290217
Epoch 616: Train Loss 0.248244 |  Val Loss 0.289863
Epoch 617: Train Loss 0.247793 |  Val Loss 0.289488
Epoch 618: Train Loss 0.247342 |  Val Loss 0.289092
Epoch 619: Train Loss 0.246890 |  Val Loss 0.288675
Epoch 620: Train Loss 0.246435 |  Val Loss 0.288236
Epoch 621: Train Loss 0.245979 |  Val Loss 0.287791
Epoch 622: Train Loss 0.245523 |  Val Loss 0.287357
Epoch 623: Train Loss 0.245069 |  Val Loss 0.286930
Epoch 624: Train Loss 0.244615 |  Val Loss 0.286500
Epoch 625: Train Loss 0.244158 |  Val Loss 0.286076
Epoch 626: Train Loss 0.243702 |  Val Loss 0.285657
Epoch 627: Train Loss 0.243247 |  Val Loss 0.285232
Epoch 628: Train Loss 0.242795 |  Val Loss 0.284830
Epoch 629: Tr

In [24]:
start_time = time.time()
XII_all_pcc95_results_df = train_with_best_hyperparameters(datasets, 'XII_all_pcc95')
elapsed_time = time.time() - start_time
print(f"Elapsed time: {elapsed_time:.2f} seconds")

[I 2025-01-04 15:56:21,080] A new study created in memory with name: no-name-5dda2c1c-c76a-417d-b222-afc36e6d3edd


Currently training NCART model with dataset key: XII_all_pcc95
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 4.632772 |  Val Loss 4.474144
Epoch 1: Train Loss 4.489971 |  Val Loss 4.344890
Epoch 2: Train Loss 4.349216 |  Val Loss 4.212892
Epoch 3: Train Loss 4.209427 |  Val Loss 4.082954
Epoch 4: Train Loss 4.069894 |  Val Loss 3.953021
Epoch 5: Train Loss 3.930629 |  Val Loss 3.822229
Epoch 6: Train Loss 3.792053 |  Val Loss 3.691552
Epoch 7: Train Loss 3.654088 |  Val Loss 3.562243
Epoch 8: Train Loss 3.516390 |  Val Loss 3.433479
Epoch 9: Train Loss 3.379174 |  Val Loss 3.304148
Epoch 10: Train Loss 3.242671 |  Val Loss 3.175626
Epoch 11: Train Loss 3.107328 |  Val Loss 3.047817
Epoch 12: Train Loss 2.972368 |  Val Loss 2.921319
Epoch 13: Train Loss 2.837786 |  Val Loss 2.796234
Epoch 14: Train Loss 2.703928 |  Val Loss 2.671859
Epoch 15: Train Loss 2.570859 |  Val Loss 2.548141
Epoch 16: Train Loss 2.438396 |  Val Loss 2.425198
Epoch 17: Train Loss 2.307147 |  Val Lo

[I 2025-01-04 15:56:23,803] Trial 0 finished with value: 0.7145252027247703 and parameters: {'n_trees': 8, 'n_selected': 28, 'n_layers': 2, 'mask_type': 'entmax'}. Best is trial 0 with value: 0.7145252027247703.


Epoch 245: Train Loss 0.076473 |  Val Loss 0.362567
Epoch 246: Train Loss 0.075675 |  Val Loss 0.362404
Validation loss has not improved for 10 steps!
Early stopping applies.
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.894748 |  Val Loss 0.783395
Epoch 1: Train Loss 0.768688 |  Val Loss 0.705958
Epoch 2: Train Loss 0.675638 |  Val Loss 0.638541
Epoch 3: Train Loss 0.603218 |  Val Loss 0.593142
Epoch 4: Train Loss 0.549486 |  Val Loss 0.565352
Epoch 5: Train Loss 0.512712 |  Val Loss 0.544877
Epoch 6: Train Loss 0.488341 |  Val Loss 0.532166
Epoch 7: Train Loss 0.471354 |  Val Loss 0.529759
Epoch 8: Train Loss 0.456820 |  Val Loss 0.524249
Epoch 9: Train Loss 0.440190 |  Val Loss 0.515203
Epoch 10: Train Loss 0.421142 |  Val Loss 0.509263
Epoch 11: Train Loss 0.400053 |  Val Loss 0.502120
Epoch 12: Train Loss 0.378147 |  Val Loss 0.482054
Epoch 13: Train Loss 0.355479 |  Val Loss 0.464390
Epoch 14: Train Loss 0.332179 |  Val Loss 0.443265
Epoch 15: Train Loss 0.309818

[I 2025-01-04 15:56:24,873] Trial 1 finished with value: 0.755 and parameters: {'n_trees': 72, 'n_selected': 32, 'n_layers': 7, 'mask_type': 'sparsemax'}. Best is trial 1 with value: 0.755.


...

Epoch 492: Train Loss 0.184942 |  Val Loss 0.343357
Epoch 493: Train Loss 0.184352 |  Val Loss 0.343334
Epoch 494: Train Loss 0.183769 |  Val Loss 0.343312
Epoch 495: Train Loss 0.183189 |  Val Loss 0.343280
Epoch 496: Train Loss 0.182613 |  Val Loss 0.343267
Epoch 497: Train Loss 0.182037 |  Val Loss 0.343265
Epoch 498: Train Loss 0.181461 |  Val Loss 0.343260
Epoch 499: Train Loss 0.180885 |  Val Loss 0.343262
Epoch 500: Train Loss 0.180309 |  Val Loss 0.343289
Epoch 501: Train Loss 0.179736 |  Val Loss 0.343312
Epoch 502: Train Loss 0.179163 |  Val Loss 0.343328
Epoch 503: Train Loss 0.178592 |  Val Loss 0.343361
Epoch 504: Train Loss 0.178020 |  Val Loss 0.343432
Epoch 505: Train Loss 0.177449 |  Val Loss 0.343509
Epoch 506: Train Loss 0.176880 |  Val Loss 0.343596
Epoch 507: Train Loss 0.176311 |  Val Loss 0.343652
Epoch 508: Train Loss 0.175742 |  Val Loss 0.343715
Epoch 509: Train Loss 0.175182 |  Val Loss 0.343765
Validation loss has not improved for 10 steps!
Early stopping ap

[I 2025-01-04 15:56:55,730] Trial 13 finished with value: 0.7966666666666666 and parameters: {'n_trees': 32, 'n_selected': 20, 'n_layers': 2, 'mask_type': 'entmax'}. Best is trial 6 with value: 0.7966666666666666.


On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.696676 |  Val Loss 0.696715
Epoch 1: Train Loss 0.695170 |  Val Loss 0.695833
Epoch 2: Train Loss 0.694084 |  Val Loss 0.695171
Epoch 3: Train Loss 0.692999 |  Val Loss 0.694191
Epoch 4: Train Loss 0.692030 |  Val Loss 0.692963
Epoch 5: Train Loss 0.691056 |  Val Loss 0.692104
Epoch 6: Train Loss 0.690071 |  Val Loss 0.691168
Epoch 7: Train Loss 0.689109 |  Val Loss 0.690390
Epoch 8: Train Loss 0.688176 |  Val Loss 0.689878
Epoch 9: Train Loss 0.687276 |  Val Loss 0.688716
Epoch 10: Train Loss 0.686372 |  Val Loss 0.687937
Epoch 11: Train Loss 0.685536 |  Val Loss 0.687172
Epoch 12: Train Loss 0.684725 |  Val Loss 0.686771
Epoch 13: Train Loss 0.683949 |  Val Loss 0.686052
Epoch 14: Train Loss 0.683195 |  Val Loss 0.685362
Epoch 15: Train Loss 0.682462 |  Val Loss 0.684664
Epoch 16: Train Loss 0.681753 |  Val Loss 0.683673
Epoch 17: Train Loss 0.681061 |  Val Loss 0.683023
Epoch 18: Train Loss 0.680387 |  Val Loss 0.682396


[I 2025-01-04 15:57:00,300] Trial 14 finished with value: 0.7966666666666666 and parameters: {'n_trees': 88, 'n_selected': 4, 'n_layers': 2, 'mask_type': 'entmax'}. Best is trial 6 with value: 0.7966666666666666.


Streaming output truncated to the last 5000 lines.
Epoch 85: Train Loss 0.542622 |  Val Loss 0.562299
Epoch 86: Train Loss 0.541334 |  Val Loss 0.561175
Epoch 87: Train Loss 0.540047 |  Val Loss 0.560058
Epoch 88: Train Loss 0.538760 |  Val Loss 0.558947
Epoch 89: Train Loss 0.537477 |  Val Loss 0.557839
Epoch 90: Train Loss 0.536197 |  Val Loss 0.556733
Epoch 91: Train Loss 0.534919 |  Val Loss 0.555636
Epoch 92: Train Loss 0.533647 |  Val Loss 0.554541
Epoch 93: Train Loss 0.532381 |  Val Loss 0.553443
Epoch 94: Train Loss 0.531119 |  Val Loss 0.552341
Epoch 95: Train Loss 0.529864 |  Val Loss 0.551237
Epoch 96: Train Loss 0.528614 |  Val Loss 0.550133
Epoch 97: Train Loss 0.527373 |  Val Loss 0.549028
Epoch 98: Train Loss 0.526132 |  Val Loss 0.547927
Epoch 99: Train Loss 0.524897 |  Val Loss 0.546834
Epoch 100: Train Loss 0.523664 |  Val Loss 0.545734
Epoch 101: Train Loss 0.522438 |  Val Loss 0.544621
Epoch 102: Train Loss 0.521218 |  Val Loss 0.543503
Epoch 103: Train Loss 0.5199

In [25]:
start_time = time.time()
XII_all_pcc75_results_df = train_with_best_hyperparameters(datasets, 'XII_all_pcc75')
elapsed_time = time.time() - start_time
print(f"Elapsed time: {elapsed_time:.2f} seconds")

[I 2025-01-04 15:57:49,004] A new study created in memory with name: no-name-db8e6eb9-adcc-4a21-9bf3-8d33d20f1546


Currently training NCART model with dataset key: XII_all_pcc75
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.878301 |  Val Loss 0.867008
Epoch 1: Train Loss 0.810699 |  Val Loss 0.812035
Epoch 2: Train Loss 0.754582 |  Val Loss 0.770366
Epoch 3: Train Loss 0.707963 |  Val Loss 0.730219
Epoch 4: Train Loss 0.669354 |  Val Loss 0.696877
Epoch 5: Train Loss 0.637141 |  Val Loss 0.671836
Epoch 6: Train Loss 0.611915 |  Val Loss 0.651275
Epoch 7: Train Loss 0.591377 |  Val Loss 0.638763
Epoch 8: Train Loss 0.574987 |  Val Loss 0.629021
Epoch 9: Train Loss 0.562702 |  Val Loss 0.620305
Epoch 10: Train Loss 0.551967 |  Val Loss 0.612429
Epoch 11: Train Loss 0.541236 |  Val Loss 0.606067
Epoch 12: Train Loss 0.530351 |  Val Loss 0.599865
Epoch 13: Train Loss 0.519556 |  Val Loss 0.591697
Epoch 14: Train Loss 0.508485 |  Val Loss 0.584363
Epoch 15: Train Loss 0.496683 |  Val Loss 0.576780
Epoch 16: Train Loss 0.484006 |  Val Loss 0.565819
Epoch 17: Train Loss 0.470190 |  Val Lo

[I 2025-01-04 15:57:50,151] Trial 0 finished with value: 0.6333333333333333 and parameters: {'n_trees': 48, 'n_selected': 24, 'n_layers': 7, 'mask_type': 'sparsemax'}. Best is trial 0 with value: 0.6333333333333333.


Epoch 40: Train Loss 0.189886 |  Val Loss 0.356322
Epoch 41: Train Loss 0.180052 |  Val Loss 0.373059
Epoch 42: Train Loss 0.171393 |  Val Loss 0.367113
Epoch 43: Train Loss 0.161597 |  Val Loss 0.367730
Epoch 44: Train Loss 0.154226 |  Val Loss 0.372891
Epoch 45: Train Loss 0.145404 |  Val Loss 0.390182
Epoch 46: Train Loss 0.139155 |  Val Loss 0.383979
Epoch 47: Train Loss 0.130344 |  Val Loss 0.370808
Epoch 48: Train Loss 0.124617 |  Val Loss 0.384631
Epoch 49: Train Loss 0.116516 |  Val Loss 0.405451
Epoch 50: Train Loss 0.110639 |  Val Loss 0.413281
Validation loss has not improved for 10 steps!
Early stopping applies.
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.701175 |  Val Loss 0.687582
Epoch 1: Train Loss 0.690952 |  Val Loss 0.679109
Epoch 2: Train Loss 0.682649 |  Val Loss 0.672747
Epoch 3: Train Loss 0.675181 |  Val Loss 0.666585
Epoch 4: Train Loss 0.668522 |  Val Loss 0.661635
Epoch 5: Train Loss 0.661949 |  Val Loss 0.656541
Epoch 6: Train Loss 0.65601

[I 2025-01-04 15:57:51,756] Trial 1 finished with value: 0.6733333333333333 and parameters: {'n_trees': 72, 'n_selected': 12, 'n_layers': 5, 'mask_type': 'entmax'}. Best is trial 1 with value: 0.6733333333333333.


...

Epoch 132: Train Loss 0.129159 |  Val Loss 0.343686
Epoch 133: Train Loss 0.125667 |  Val Loss 0.343363
Epoch 134: Train Loss 0.123714 |  Val Loss 0.341784
Epoch 135: Train Loss 0.120829 |  Val Loss 0.339838
Epoch 136: Train Loss 0.118504 |  Val Loss 0.340491
Validation loss has not improved for 10 steps!
Early stopping applies.
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.682561 |  Val Loss 0.665577
Epoch 1: Train Loss 0.669233 |  Val Loss 0.658142
Epoch 2: Train Loss 0.658952 |  Val Loss 0.652662
Epoch 3: Train Loss 0.650581 |  Val Loss 0.644985
Epoch 4: Train Loss 0.642687 |  Val Loss 0.637989
Epoch 5: Train Loss 0.634852 |  Val Loss 0.629955
Epoch 6: Train Loss 0.627056 |  Val Loss 0.622686
Epoch 7: Train Loss 0.619374 |  Val Loss 0.616159
Epoch 8: Train Loss 0.611617 |  Val Loss 0.610724
Epoch 9: Train Loss 0.604136 |  Val Loss 0.605466
Epoch 10: Train Loss 0.596835 |  Val Loss 0.599794
Epoch 11: Train Loss 0.589671 |  Val Loss 0.593932
Epoch 12: Train Loss 0.582

[I 2025-01-04 15:58:34,412] Trial 13 finished with value: 0.7966666666666666 and parameters: {'n_trees': 40, 'n_selected': 20, 'n_layers': 3, 'mask_type': 'sparsemax'}. Best is trial 11 with value: 0.8013876853447538.


Epoch 117: Train Loss 0.036105 |  Val Loss 0.237051
Epoch 118: Train Loss 0.034953 |  Val Loss 0.238755
Epoch 119: Train Loss 0.033899 |  Val Loss 0.238846
Epoch 120: Train Loss 0.032850 |  Val Loss 0.239149
Epoch 121: Train Loss 0.031893 |  Val Loss 0.239993
Epoch 122: Train Loss 0.030946 |  Val Loss 0.241404
Epoch 123: Train Loss 0.030072 |  Val Loss 0.241050
Epoch 124: Train Loss 0.029387 |  Val Loss 0.243054
Validation loss has not improved for 10 steps!
Early stopping applies.
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.696085 |  Val Loss 0.691406
Epoch 1: Train Loss 0.695126 |  Val Loss 0.690737
Epoch 2: Train Loss 0.694204 |  Val Loss 0.690090
Epoch 3: Train Loss 0.693334 |  Val Loss 0.689447
Epoch 4: Train Loss 0.692494 |  Val Loss 0.688794
Epoch 5: Train Loss 0.691680 |  Val Loss 0.688138
Epoch 6: Train Loss 0.690879 |  Val Loss 0.687481
Epoch 7: Train Loss 0.690083 |  Val Loss 0.686787
Epoch 8: Train Loss 0.689297 |  Val Loss 0.686128
Epoch 9: Train Loss 0.

[I 2025-01-04 15:58:38,475] Trial 14 finished with value: 0.755 and parameters: {'n_trees': 96, 'n_selected': 4, 'n_layers': 2, 'mask_type': 'sparsemax'}. Best is trial 11 with value: 0.8013876853447538.


Epoch 344: Train Loss 0.126064 |  Val Loss 0.368065
Epoch 345: Train Loss 0.124770 |  Val Loss 0.366559
Epoch 346: Train Loss 0.123494 |  Val Loss 0.368842
Epoch 347: Train Loss 0.122262 |  Val Loss 0.370878
Epoch 348: Train Loss 0.120994 |  Val Loss 0.365696
Epoch 349: Train Loss 0.119858 |  Val Loss 0.366422
Epoch 350: Train Loss 0.118585 |  Val Loss 0.370420
Epoch 351: Train Loss 0.117517 |  Val Loss 0.368370
Epoch 352: Train Loss 0.116367 |  Val Loss 0.367256
Epoch 353: Train Loss 0.115204 |  Val Loss 0.368905
Epoch 354: Train Loss 0.114043 |  Val Loss 0.368133
Epoch 355: Train Loss 0.112915 |  Val Loss 0.367121
Epoch 356: Train Loss 0.111846 |  Val Loss 0.369854
Epoch 357: Train Loss 0.110751 |  Val Loss 0.368935
Epoch 358: Train Loss 0.109704 |  Val Loss 0.366060
Epoch 359: Train Loss 0.108631 |  Val Loss 0.369061
Validation loss has not improved for 10 steps!
Early stopping applies.
Best hyperparameters: {'n_trees': 128, 'n_selected': 20, 'n_layers': 3, 'mask_type': 'sparsemax'}

In [26]:
start_time = time.time()
XII_200_nopcc_results_df = train_with_best_hyperparameters(datasets, 'XII_200_nopcc')
elapsed_time = time.time() - start_time
print(f"Elapsed time: {elapsed_time:.2f} seconds")

[I 2025-01-04 15:58:52,317] A new study created in memory with name: no-name-8044b011-a43e-4182-b235-982c6ee46835


Currently training NCART model with dataset key: XII_200_nopcc
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.699561 |  Val Loss 0.676373
Epoch 1: Train Loss 0.678535 |  Val Loss 0.667050
Epoch 2: Train Loss 0.663150 |  Val Loss 0.658136
Epoch 3: Train Loss 0.650065 |  Val Loss 0.650580
Epoch 4: Train Loss 0.637629 |  Val Loss 0.642266
Epoch 5: Train Loss 0.624831 |  Val Loss 0.633139
Epoch 6: Train Loss 0.611062 |  Val Loss 0.623184
Epoch 7: Train Loss 0.596491 |  Val Loss 0.612404
Epoch 8: Train Loss 0.581883 |  Val Loss 0.601309
Epoch 9: Train Loss 0.567279 |  Val Loss 0.591332
Epoch 10: Train Loss 0.552799 |  Val Loss 0.580174
Epoch 11: Train Loss 0.537824 |  Val Loss 0.569576
Epoch 12: Train Loss 0.523151 |  Val Loss 0.560083
Epoch 13: Train Loss 0.509373 |  Val Loss 0.550238
Epoch 14: Train Loss 0.496252 |  Val Loss 0.541121
Epoch 15: Train Loss 0.483432 |  Val Loss 0.533909
Epoch 16: Train Loss 0.470648 |  Val Loss 0.527178
Epoch 17: Train Loss 0.458055 |  Val Lo

[I 2025-01-04 15:58:54,219] Trial 0 finished with value: 0.7 and parameters: {'n_trees': 120, 'n_selected': 12, 'n_layers': 7, 'mask_type': 'sparsemax'}. Best is trial 0 with value: 0.7.


On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.980138 |  Val Loss 0.896233
Epoch 1: Train Loss 0.903474 |  Val Loss 0.842215
Epoch 2: Train Loss 0.839427 |  Val Loss 0.795864
Epoch 3: Train Loss 0.784290 |  Val Loss 0.753932
Epoch 4: Train Loss 0.734064 |  Val Loss 0.718091
Epoch 5: Train Loss 0.688552 |  Val Loss 0.680550
Epoch 6: Train Loss 0.647029 |  Val Loss 0.646110
Epoch 7: Train Loss 0.609435 |  Val Loss 0.614149
Epoch 8: Train Loss 0.575015 |  Val Loss 0.586274
Epoch 9: Train Loss 0.543359 |  Val Loss 0.558858
Epoch 10: Train Loss 0.514522 |  Val Loss 0.536111
Epoch 11: Train Loss 0.488895 |  Val Loss 0.515553
Epoch 12: Train Loss 0.465417 |  Val Loss 0.497817
Epoch 13: Train Loss 0.444278 |  Val Loss 0.484327
Epoch 14: Train Loss 0.425500 |  Val Loss 0.472647
Epoch 15: Train Loss 0.408228 |  Val Loss 0.460567
Epoch 16: Train Loss 0.392001 |  Val Loss 0.451024
Epoch 17: Train Loss 0.377500 |  Val Loss 0.443243
Epoch 18: Train Loss 0.363678 |  Val Loss 0.435633


[I 2025-01-04 15:58:55,564] Trial 1 finished with value: 0.7509392614826383 and parameters: {'n_trees': 64, 'n_selected': 20, 'n_layers': 5, 'mask_type': 'sparsemax'}. Best is trial 1 with value: 0.7509392614826383.


...

Epoch 78: Train Loss 0.099278 |  Val Loss 0.333881
Epoch 79: Train Loss 0.096980 |  Val Loss 0.336773
Epoch 80: Train Loss 0.094589 |  Val Loss 0.339637
Epoch 81: Train Loss 0.092418 |  Val Loss 0.337335
Epoch 82: Train Loss 0.090185 |  Val Loss 0.335596
Epoch 83: Train Loss 0.088130 |  Val Loss 0.337934
Epoch 84: Train Loss 0.086023 |  Val Loss 0.340799
Epoch 85: Train Loss 0.084079 |  Val Loss 0.339390
Epoch 86: Train Loss 0.082104 |  Val Loss 0.339347
Epoch 87: Train Loss 0.080260 |  Val Loss 0.342991
Epoch 88: Train Loss 0.078399 |  Val Loss 0.344975
Epoch 89: Train Loss 0.076641 |  Val Loss 0.343803
Validation loss has not improved for 10 steps!
Early stopping applies.
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.692981 |  Val Loss 0.685151
Epoch 1: Train Loss 0.686087 |  Val Loss 0.681839
Epoch 2: Train Loss 0.680737 |  Val Loss 0.677608
Epoch 3: Train Loss 0.675960 |  Val Loss 0.673045
Epoch 4: Train Loss 0.671627 |  Val Loss 0.670796
Epoch 5: Train Loss 0.6674

[I 2025-01-04 15:59:34,828] Trial 13 finished with value: 0.8510644963469901 and parameters: {'n_trees': 40, 'n_selected': 8, 'n_layers': 3, 'mask_type': 'entmax'}. Best is trial 2 with value: 0.9045340337332909.


Epoch 134: Train Loss 0.143370 |  Val Loss 0.344183
Epoch 135: Train Loss 0.141109 |  Val Loss 0.336331
Epoch 136: Train Loss 0.138563 |  Val Loss 0.338089
Epoch 137: Train Loss 0.136252 |  Val Loss 0.342398
Epoch 138: Train Loss 0.134160 |  Val Loss 0.332268
Epoch 139: Train Loss 0.131942 |  Val Loss 0.329901
Epoch 140: Train Loss 0.130193 |  Val Loss 0.338421
Validation loss has not improved for 10 steps!
Early stopping applies.
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.955783 |  Val Loss 0.936566
Epoch 1: Train Loss 0.908471 |  Val Loss 0.902932
Epoch 2: Train Loss 0.867801 |  Val Loss 0.869466
Epoch 3: Train Loss 0.831959 |  Val Loss 0.837663
Epoch 4: Train Loss 0.796346 |  Val Loss 0.804824
Epoch 5: Train Loss 0.763247 |  Val Loss 0.776608
Epoch 6: Train Loss 0.732079 |  Val Loss 0.751292
Epoch 7: Train Loss 0.702516 |  Val Loss 0.725501
Epoch 8: Train Loss 0.673056 |  Val Loss 0.700138
Epoch 9: Train Loss 0.645090 |  Val Loss 0.678264
Epoch 10: Train Loss 0.6

[I 2025-01-04 15:59:37,086] Trial 14 finished with value: 0.7509392614826383 and parameters: {'n_trees': 80, 'n_selected': 16, 'n_layers': 6, 'mask_type': 'sparsemax'}. Best is trial 2 with value: 0.9045340337332909.


 Val Loss 0.239914
Epoch 114: Train Loss 0.047374 |  Val Loss 0.239239
Epoch 115: Train Loss 0.046576 |  Val Loss 0.238484
Epoch 116: Train Loss 0.045798 |  Val Loss 0.238675
Epoch 117: Train Loss 0.045038 |  Val Loss 0.239443
Epoch 118: Train Loss 0.044298 |  Val Loss 0.239811
Validation loss has not improved for 10 steps!
Early stopping applies.
Best hyperparameters: {'n_trees': 56, 'n_selected': 16, 'n_layers': 6, 'mask_type': 'entmax'}
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.799003 |  Val Loss 0.746884
Epoch 1: Train Loss 0.760902 |  Val Loss 0.724948
Epoch 2: Train Loss 0.728634 |  Val Loss 0.703666
Epoch 3: Train Loss 0.701979 |  Val Loss 0.685975
Epoch 4: Train Loss 0.678512 |  Val Loss 0.669764
Epoch 5: Train Loss 0.657343 |  Val Loss 0.655461
Epoch 6: Train Loss 0.637236 |  Val Loss 0.641623
Epoch 7: Train Loss 0.618524 |  Val Loss 0.627211
Epoch 8: Train Loss 0.601309 |  Val Loss 0.614822
Epoch 9: Train Loss 0.585354 |  Val Loss 0.602561
Epoch 10: Train

In [27]:
start_time = time.time()
XII_200_pcc95_results_df = train_with_best_hyperparameters(datasets, 'XII_200_pcc95')
elapsed_time = time.time() - start_time
print(f"Elapsed time: {elapsed_time:.2f} seconds")

[I 2025-01-04 15:59:58,879] A new study created in memory with name: no-name-352e5090-5c2a-4d09-886c-28751dfe1539


Currently training NCART model with dataset key: XII_200_pcc95
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.699766 |  Val Loss 0.664083
Epoch 1: Train Loss 0.644415 |  Val Loss 0.654407
Epoch 2: Train Loss 0.616736 |  Val Loss 0.634815
Epoch 3: Train Loss 0.589411 |  Val Loss 0.616839
Epoch 4: Train Loss 0.563030 |  Val Loss 0.595397
Epoch 5: Train Loss 0.535825 |  Val Loss 0.581599
Epoch 6: Train Loss 0.511398 |  Val Loss 0.565297
Epoch 7: Train Loss 0.487451 |  Val Loss 0.548338
Epoch 8: Train Loss 0.462701 |  Val Loss 0.530554
Epoch 9: Train Loss 0.437205 |  Val Loss 0.512035
Epoch 10: Train Loss 0.411307 |  Val Loss 0.489445
Epoch 11: Train Loss 0.385610 |  Val Loss 0.474373
Epoch 12: Train Loss 0.360249 |  Val Loss 0.455340
Epoch 13: Train Loss 0.334649 |  Val Loss 0.439623
Epoch 14: Train Loss 0.309099 |  Val Loss 0.427863
Epoch 15: Train Loss 0.284572 |  Val Loss 0.413850
Epoch 16: Train Loss 0.261359 |  Val Loss 0.397925
Epoch 17: Train Loss 0.239782 |  Val Lo

[I 2025-01-04 16:00:00,249] Trial 0 finished with value: 0.7509392614826383 and parameters: {'n_trees': 120, 'n_selected': 32, 'n_layers': 8, 'mask_type': 'entmax'}. Best is trial 0 with value: 0.7509392614826383.


Epoch 51: Train Loss 0.018034 |  Val Loss 0.336093
Validation loss has not improved for 10 steps!
Early stopping applies.
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.730025 |  Val Loss 0.731099
Epoch 1: Train Loss 0.722921 |  Val Loss 0.727473
Epoch 2: Train Loss 0.717035 |  Val Loss 0.722623
Epoch 3: Train Loss 0.711973 |  Val Loss 0.718262
Epoch 4: Train Loss 0.706940 |  Val Loss 0.714725
Epoch 5: Train Loss 0.701803 |  Val Loss 0.711179
Epoch 6: Train Loss 0.696835 |  Val Loss 0.707416
Epoch 7: Train Loss 0.691956 |  Val Loss 0.703234
Epoch 8: Train Loss 0.687214 |  Val Loss 0.700125
Epoch 9: Train Loss 0.682407 |  Val Loss 0.696139
Epoch 10: Train Loss 0.677661 |  Val Loss 0.691730
Epoch 11: Train Loss 0.672793 |  Val Loss 0.687261
Epoch 12: Train Loss 0.667867 |  Val Loss 0.682936
Epoch 13: Train Loss 0.663081 |  Val Loss 0.678495
Epoch 14: Train Loss 0.658534 |  Val Loss 0.674389
Epoch 15: Train Loss 0.654157 |  Val Loss 0.670644
Epoch 16: Train Loss 0.649817 |

[I 2025-01-04 16:00:06,775] Trial 1 finished with value: 0.8 and parameters: {'n_trees': 96, 'n_selected': 4, 'n_layers': 8, 'mask_type': 'sparsemax'}. Best is trial 1 with value: 0.8.


...

Epoch 326: Train Loss 0.150752 |  Val Loss 0.452120
Epoch 327: Train Loss 0.149621 |  Val Loss 0.452155
Epoch 328: Train Loss 0.148516 |  Val Loss 0.450900
Epoch 329: Train Loss 0.147417 |  Val Loss 0.450526
Epoch 330: Train Loss 0.146327 |  Val Loss 0.449698
Epoch 331: Train Loss 0.145242 |  Val Loss 0.450503
Epoch 332: Train Loss 0.144165 |  Val Loss 0.451409
Validation loss has not improved for 10 steps!
Early stopping applies.
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.720379 |  Val Loss 0.700774
Epoch 1: Train Loss 0.698720 |  Val Loss 0.692303
Epoch 2: Train Loss 0.685882 |  Val Loss 0.681850
Epoch 3: Train Loss 0.670473 |  Val Loss 0.671975
Epoch 4: Train Loss 0.660192 |  Val Loss 0.665053
Epoch 5: Train Loss 0.651291 |  Val Loss 0.658636
Epoch 6: Train Loss 0.642810 |  Val Loss 0.653284
Epoch 7: Train Loss 0.634897 |  Val Loss 0.649813
Epoch 8: Train Loss 0.628443 |  Val Loss 0.648355
Epoch 9: Train Loss 0.622593 |  Val Loss 0.645413
Epoch 10: Train Loss 0.6

[I 2025-01-04 16:00:49,063] Trial 13 finished with value: 0.7035264706814485 and parameters: {'n_trees': 128, 'n_selected': 16, 'n_layers': 4, 'mask_type': 'entmax'}. Best is trial 4 with value: 0.9.


Epoch 88: Train Loss 0.079068 |  Val Loss 0.362647
Epoch 89: Train Loss 0.076766 |  Val Loss 0.360946
Validation loss has not improved for 10 steps!
Early stopping applies.
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.714449 |  Val Loss 0.711004
Epoch 1: Train Loss 0.712039 |  Val Loss 0.708889
Epoch 2: Train Loss 0.709782 |  Val Loss 0.706932
Epoch 3: Train Loss 0.707682 |  Val Loss 0.705133
Epoch 4: Train Loss 0.705737 |  Val Loss 0.703490
Epoch 5: Train Loss 0.703946 |  Val Loss 0.702003
Epoch 6: Train Loss 0.702308 |  Val Loss 0.700673
Epoch 7: Train Loss 0.700822 |  Val Loss 0.699498
Epoch 8: Train Loss 0.699481 |  Val Loss 0.698464
Epoch 9: Train Loss 0.698283 |  Val Loss 0.697565
Epoch 10: Train Loss 0.697217 |  Val Loss 0.696783
Epoch 11: Train Loss 0.696279 |  Val Loss 0.696118
Epoch 12: Train Loss 0.695457 |  Val Loss 0.695560
Epoch 13: Train Loss 0.694739 |  Val Loss 0.695099
Epoch 14: Train Loss 0.694114 |  Val Loss 0.694720
Epoch 15: Train Loss 0.693569 |

[I 2025-01-04 16:00:54,116] Trial 14 finished with value: 0.6030226891555273 and parameters: {'n_trees': 96, 'n_selected': 8, 'n_layers': 1, 'mask_type': 'entmax'}. Best is trial 4 with value: 0.9.


Epoch 525: Train Loss 0.337715 |  Val Loss 0.460916
Epoch 526: Train Loss 0.337038 |  Val Loss 0.460921
Epoch 527: Train Loss 0.336361 |  Val Loss 0.460927
Epoch 528: Train Loss 0.335685 |  Val Loss 0.460935
Epoch 529: Train Loss 0.335010 |  Val Loss 0.460951
Epoch 530: Train Loss 0.334336 |  Val Loss 0.460980
Epoch 531: Train Loss 0.333664 |  Val Loss 0.461012
Epoch 532: Train Loss 0.332994 |  Val Loss 0.461046
Epoch 533: Train Loss 0.332328 |  Val Loss 0.461076
Epoch 534: Train Loss 0.331664 |  Val Loss 0.461105
Epoch 535: Train Loss 0.331002 |  Val Loss 0.461139
Epoch 536: Train Loss 0.330342 |  Val Loss 0.461176
Validation loss has not improved for 10 steps!
Early stopping applies.
Best hyperparameters: {'n_trees': 112, 'n_selected': 8, 'n_layers': 5, 'mask_type': 'entmax'}
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.720468 |  Val Loss 0.716420
Epoch 1: Train Loss 0.711619 |  Val Loss 0.710937
Epoch 2: Train Loss 0.705141 |  Val Loss 0.707251
Epoch 3: Train Loss 

In [28]:
start_time = time.time()
XII_200_pcc75_results_df = train_with_best_hyperparameters(datasets, 'XII_200_pcc75')
elapsed_time = time.time() - start_time
print(f"Elapsed time: {elapsed_time:.2f} seconds")

[I 2025-01-04 16:01:37,642] A new study created in memory with name: no-name-4f6b4739-183b-4c41-8936-1cc42f25a475


Currently training NCART model with dataset key: XII_200_pcc75
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.706439 |  Val Loss 0.703944
Epoch 1: Train Loss 0.704539 |  Val Loss 0.702722
Epoch 2: Train Loss 0.702869 |  Val Loss 0.701872
Epoch 3: Train Loss 0.701318 |  Val Loss 0.701182
Epoch 4: Train Loss 0.699990 |  Val Loss 0.700528
Epoch 5: Train Loss 0.698700 |  Val Loss 0.699568
Epoch 6: Train Loss 0.697429 |  Val Loss 0.698818
Epoch 7: Train Loss 0.696116 |  Val Loss 0.697678
Epoch 8: Train Loss 0.694836 |  Val Loss 0.696602
Epoch 9: Train Loss 0.693552 |  Val Loss 0.695336
Epoch 10: Train Loss 0.692319 |  Val Loss 0.694392
Epoch 11: Train Loss 0.691151 |  Val Loss 0.693451
Epoch 12: Train Loss 0.689997 |  Val Loss 0.692636
Epoch 13: Train Loss 0.688839 |  Val Loss 0.691699
Epoch 14: Train Loss 0.687734 |  Val Loss 0.690893
Epoch 15: Train Loss 0.686669 |  Val Loss 0.690122
Epoch 16: Train Loss 0.685633 |  Val Loss 0.689303
Epoch 17: Train Loss 0.684598 |  Val Lo

[I 2025-01-04 16:01:41,528] Trial 0 finished with value: 0.6 and parameters: {'n_trees': 48, 'n_selected': 4, 'n_layers': 4, 'mask_type': 'sparsemax'}. Best is trial 0 with value: 0.6.


Validation loss has not improved for 10 steps!
Early stopping applies.
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.811869 |  Val Loss 0.785048
Epoch 1: Train Loss 0.792931 |  Val Loss 0.770498
Epoch 2: Train Loss 0.775519 |  Val Loss 0.756188
Epoch 3: Train Loss 0.760138 |  Val Loss 0.745359
Epoch 4: Train Loss 0.745188 |  Val Loss 0.734161
Epoch 5: Train Loss 0.731280 |  Val Loss 0.722240
Epoch 6: Train Loss 0.718035 |  Val Loss 0.712443
Epoch 7: Train Loss 0.705254 |  Val Loss 0.703150
Epoch 8: Train Loss 0.693118 |  Val Loss 0.693825
Epoch 9: Train Loss 0.681548 |  Val Loss 0.684403
Epoch 10: Train Loss 0.670397 |  Val Loss 0.675521
Epoch 11: Train Loss 0.659648 |  Val Loss 0.667261
Epoch 12: Train Loss 0.649312 |  Val Loss 0.659736
Epoch 13: Train Loss 0.639504 |  Val Loss 0.653191
Epoch 14: Train Loss 0.630047 |  Val Loss 0.646531
Epoch 15: Train Loss 0.620915 |  Val Loss 0.639826
Epoch 16: Train Loss 0.612406 |  Val Loss 0.633705
Epoch 17: Train Loss 0.604028 |

[I 2025-01-04 16:01:43,105] Trial 1 finished with value: 0.5506887917539348 and parameters: {'n_trees': 56, 'n_selected': 12, 'n_layers': 6, 'mask_type': 'sparsemax'}. Best is trial 0 with value: 0.6.


...

Epoch 114: Train Loss 0.204005 |  Val Loss 0.454104
Validation loss has not improved for 10 steps!
Early stopping applies.
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.743404 |  Val Loss 0.722097
Epoch 1: Train Loss 0.722860 |  Val Loss 0.708255
Epoch 2: Train Loss 0.705460 |  Val Loss 0.696635
Epoch 3: Train Loss 0.690082 |  Val Loss 0.687418
Epoch 4: Train Loss 0.676978 |  Val Loss 0.679925
Epoch 5: Train Loss 0.665591 |  Val Loss 0.674514
Epoch 6: Train Loss 0.656691 |  Val Loss 0.669710
Epoch 7: Train Loss 0.649264 |  Val Loss 0.665212
Epoch 8: Train Loss 0.642620 |  Val Loss 0.660989
Epoch 9: Train Loss 0.635731 |  Val Loss 0.656736
Epoch 10: Train Loss 0.628604 |  Val Loss 0.652323
Epoch 11: Train Loss 0.621225 |  Val Loss 0.646823
Epoch 12: Train Loss 0.613107 |  Val Loss 0.639731
Epoch 13: Train Loss 0.604268 |  Val Loss 0.632303
Epoch 14: Train Loss 0.594864 |  Val Loss 0.624058
Epoch 15: Train Loss 0.584985 |  Val Loss 0.615542
Epoch 16: Train Loss 0.574538 

[I 2025-01-04 16:02:05,360] Trial 13 finished with value: 0.7 and parameters: {'n_trees': 128, 'n_selected': 20, 'n_layers': 6, 'mask_type': 'entmax'}. Best is trial 3 with value: 0.7509392614826383.


Epoch 75: Train Loss 0.089355 |  Val Loss 0.358075
Epoch 76: Train Loss 0.086591 |  Val Loss 0.359432
Epoch 77: Train Loss 0.083981 |  Val Loss 0.357768
Epoch 78: Train Loss 0.081508 |  Val Loss 0.358079
Epoch 79: Train Loss 0.079141 |  Val Loss 0.358827
Epoch 80: Train Loss 0.076828 |  Val Loss 0.360632
Validation loss has not improved for 10 steps!
Early stopping applies.
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.792526 |  Val Loss 0.770881
Epoch 1: Train Loss 0.767876 |  Val Loss 0.755067
Epoch 2: Train Loss 0.745711 |  Val Loss 0.747933
Epoch 3: Train Loss 0.727613 |  Val Loss 0.737248
Epoch 4: Train Loss 0.710189 |  Val Loss 0.725383
Epoch 5: Train Loss 0.692913 |  Val Loss 0.711822
Epoch 6: Train Loss 0.676059 |  Val Loss 0.698344
Epoch 7: Train Loss 0.660507 |  Val Loss 0.687232
Epoch 8: Train Loss 0.645854 |  Val Loss 0.674906
Epoch 9: Train Loss 0.632045 |  Val Loss 0.663779
Epoch 10: Train Loss 0.619142 |  Val Loss 0.653454
Epoch 11: Train Loss 0.606922 |

[I 2025-01-04 16:02:07,234] Trial 14 finished with value: 0.6030226891555273 and parameters: {'n_trees': 80, 'n_selected': 12, 'n_layers': 8, 'mask_type': 'sparsemax'}. Best is trial 3 with value: 0.7509392614826383.


Epoch 75: Train Loss 0.174982 |  Val Loss 0.423088
Epoch 76: Train Loss 0.171689 |  Val Loss 0.415552
Epoch 77: Train Loss 0.168465 |  Val Loss 0.417433
Epoch 78: Train Loss 0.165291 |  Val Loss 0.418690
Epoch 79: Train Loss 0.162197 |  Val Loss 0.418136
Epoch 80: Train Loss 0.159178 |  Val Loss 0.413741
Epoch 81: Train Loss 0.156222 |  Val Loss 0.412244
Epoch 82: Train Loss 0.153325 |  Val Loss 0.414846
Epoch 83: Train Loss 0.150494 |  Val Loss 0.416124
Validation loss has not improved for 10 steps!
Early stopping applies.
Best hyperparameters: {'n_trees': 72, 'n_selected': 28, 'n_layers': 8, 'mask_type': 'entmax'}
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.734282 |  Val Loss 0.691245
Epoch 1: Train Loss 0.694240 |  Val Loss 0.671550
Epoch 2: Train Loss 0.664409 |  Val Loss 0.656116
Epoch 3: Train Loss 0.642289 |  Val Loss 0.643517
Epoch 4: Train Loss 0.625831 |  Val Loss 0.632696
Epoch 5: Train Loss 0.611887 |  Val Loss 0.623722
Epoch 6: Train Loss 0.597655 |  Val

In [29]:
start_time = time.time()
XII_150_nopcc_results_df = train_with_best_hyperparameters(datasets, 'XII_150_nopcc')
elapsed_time = time.time() - start_time
print(f"Elapsed time: {elapsed_time:.2f} seconds")

[I 2025-01-04 16:02:21,215] A new study created in memory with name: no-name-a1d79651-8ce7-4d73-ab52-0db969d617b6


Currently training NCART model with dataset key: XII_150_nopcc
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.919623 |  Val Loss 0.898468
Epoch 1: Train Loss 0.850970 |  Val Loss 0.837350
Epoch 2: Train Loss 0.795642 |  Val Loss 0.781293
Epoch 3: Train Loss 0.747649 |  Val Loss 0.744488
Epoch 4: Train Loss 0.706436 |  Val Loss 0.718251
Epoch 5: Train Loss 0.674574 |  Val Loss 0.687152
Epoch 6: Train Loss 0.648831 |  Val Loss 0.657125
Epoch 7: Train Loss 0.629732 |  Val Loss 0.642756
Epoch 8: Train Loss 0.616830 |  Val Loss 0.633157
Epoch 9: Train Loss 0.608551 |  Val Loss 0.627275
Epoch 10: Train Loss 0.603020 |  Val Loss 0.622830
Epoch 11: Train Loss 0.599099 |  Val Loss 0.618327
Epoch 12: Train Loss 0.595084 |  Val Loss 0.611350
Epoch 13: Train Loss 0.590480 |  Val Loss 0.612123
Epoch 14: Train Loss 0.584670 |  Val Loss 0.604626
Epoch 15: Train Loss 0.577295 |  Val Loss 0.596339
Epoch 16: Train Loss 0.568734 |  Val Loss 0.586686
Epoch 17: Train Loss 0.558844 |  Val Lo

[I 2025-01-04 16:02:22,827] Trial 0 finished with value: 0.8017837257372731 and parameters: {'n_trees': 48, 'n_selected': 28, 'n_layers': 2, 'mask_type': 'sparsemax'}. Best is trial 0 with value: 0.8017837257372731.


|  Val Loss 0.273904
Epoch 156: Train Loss 0.028231 |  Val Loss 0.273352
Epoch 157: Train Loss 0.027792 |  Val Loss 0.273445
Epoch 158: Train Loss 0.027166 |  Val Loss 0.274149
Validation loss has not improved for 10 steps!
Early stopping applies.
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.882641 |  Val Loss 0.857764
Epoch 1: Train Loss 0.854009 |  Val Loss 0.834733
Epoch 2: Train Loss 0.831913 |  Val Loss 0.812131
Epoch 3: Train Loss 0.811127 |  Val Loss 0.794231
Epoch 4: Train Loss 0.791188 |  Val Loss 0.776633
Epoch 5: Train Loss 0.772387 |  Val Loss 0.759113
Epoch 6: Train Loss 0.754620 |  Val Loss 0.741744
Epoch 7: Train Loss 0.737296 |  Val Loss 0.724480
Epoch 8: Train Loss 0.720589 |  Val Loss 0.707441
Epoch 9: Train Loss 0.704287 |  Val Loss 0.691925
Epoch 10: Train Loss 0.688824 |  Val Loss 0.678150
Epoch 11: Train Loss 0.673872 |  Val Loss 0.666035
Epoch 12: Train Loss 0.659513 |  Val Loss 0.654634
Epoch 13: Train Loss 0.645880 |  Val Loss 0.643592
Epoch 1

[I 2025-01-04 16:02:26,191] Trial 1 finished with value: 0.8666666666666667 and parameters: {'n_trees': 88, 'n_selected': 12, 'n_layers': 4, 'mask_type': 'entmax'}. Best is trial 1 with value: 0.8666666666666667.


...

Epoch 109: Train Loss 0.062186 |  Val Loss 0.255052
Epoch 110: Train Loss 0.060978 |  Val Loss 0.257040
Epoch 111: Train Loss 0.059878 |  Val Loss 0.255605
Epoch 112: Train Loss 0.058774 |  Val Loss 0.252554
Epoch 113: Train Loss 0.057688 |  Val Loss 0.251697
Epoch 114: Train Loss 0.056643 |  Val Loss 0.252411
Epoch 115: Train Loss 0.055620 |  Val Loss 0.253157
Epoch 116: Train Loss 0.054633 |  Val Loss 0.253428
Epoch 117: Train Loss 0.053669 |  Val Loss 0.253029
Epoch 118: Train Loss 0.052729 |  Val Loss 0.252371
Epoch 119: Train Loss 0.051818 |  Val Loss 0.252216
Epoch 120: Train Loss 0.050928 |  Val Loss 0.252678
Epoch 121: Train Loss 0.050071 |  Val Loss 0.252124
Epoch 122: Train Loss 0.049231 |  Val Loss 0.252083
Epoch 123: Train Loss 0.048399 |  Val Loss 0.252284
Epoch 124: Train Loss 0.047586 |  Val Loss 0.252888
Validation loss has not improved for 10 steps!
Early stopping applies.
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.700300 |  Val Loss 0.691100
Epoch 

[I 2025-01-04 16:02:53,121] Trial 13 finished with value: 0.9354143466934853 and parameters: {'n_trees': 64, 'n_selected': 8, 'n_layers': 5, 'mask_type': 'sparsemax'}. Best is trial 5 with value: 0.9354143466934853.


Epoch 129: Train Loss 0.090093 |  Val Loss 0.246639
Epoch 130: Train Loss 0.088704 |  Val Loss 0.248621
Epoch 131: Train Loss 0.087309 |  Val Loss 0.245864
Epoch 132: Train Loss 0.085927 |  Val Loss 0.243872
Epoch 133: Train Loss 0.084618 |  Val Loss 0.245074
Epoch 134: Train Loss 0.083323 |  Val Loss 0.246359
Validation loss has not improved for 10 steps!
Early stopping applies.
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.692328 |  Val Loss 0.688141
Epoch 1: Train Loss 0.684838 |  Val Loss 0.682848
Epoch 2: Train Loss 0.679484 |  Val Loss 0.678133
Epoch 3: Train Loss 0.674086 |  Val Loss 0.674941
Epoch 4: Train Loss 0.669884 |  Val Loss 0.670729
Epoch 5: Train Loss 0.665352 |  Val Loss 0.665131
Epoch 6: Train Loss 0.659907 |  Val Loss 0.660179
Epoch 7: Train Loss 0.653810 |  Val Loss 0.656026
Epoch 8: Train Loss 0.649074 |  Val Loss 0.651780
Epoch 9: Train Loss 0.644387 |  Val Loss 0.647730
Epoch 10: Train Loss 0.639873 |  Val Loss 0.643716
Epoch 11: Train Loss 0.63

[I 2025-01-04 16:02:59,460] Trial 14 finished with value: 0.8666666666666667 and parameters: {'n_trees': 64, 'n_selected': 4, 'n_layers': 6, 'mask_type': 'sparsemax'}. Best is trial 5 with value: 0.9354143466934853.


Epoch 374: Train Loss 0.051204 |  Val Loss 0.217384
Epoch 375: Train Loss 0.050868 |  Val Loss 0.218485
Epoch 376: Train Loss 0.050523 |  Val Loss 0.217525
Epoch 377: Train Loss 0.050185 |  Val Loss 0.217712
Validation loss has not improved for 10 steps!
Early stopping applies.
Best hyperparameters: {'n_trees': 64, 'n_selected': 12, 'n_layers': 7, 'mask_type': 'sparsemax'}
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.899991 |  Val Loss 0.883790
Epoch 1: Train Loss 0.865930 |  Val Loss 0.848481
Epoch 2: Train Loss 0.831248 |  Val Loss 0.821957
Epoch 3: Train Loss 0.800441 |  Val Loss 0.794844
Epoch 4: Train Loss 0.772100 |  Val Loss 0.770235
Epoch 5: Train Loss 0.744097 |  Val Loss 0.747075
Epoch 6: Train Loss 0.716894 |  Val Loss 0.722360
Epoch 7: Train Loss 0.691871 |  Val Loss 0.696276
Epoch 8: Train Loss 0.666861 |  Val Loss 0.672316
Epoch 9: Train Loss 0.642204 |  Val Loss 0.650529
Epoch 10: Train Loss 0.618484 |  Val Loss 0.629911
Epoch 11: Train Loss 0.595490 | 

In [30]:
start_time = time.time()
XII_150_pcc95_results_df = train_with_best_hyperparameters(datasets, 'XII_150_pcc95')
elapsed_time = time.time() - start_time
print(f"Elapsed time: {elapsed_time:.2f} seconds")

[I 2025-01-04 16:03:27,706] A new study created in memory with name: no-name-dbdafb7a-ca3b-4738-96a4-c8d22a9a4554


Currently training NCART model with dataset key: XII_150_pcc95
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.730672 |  Val Loss 0.712798
Epoch 1: Train Loss 0.721283 |  Val Loss 0.704720
Epoch 2: Train Loss 0.712874 |  Val Loss 0.697647
Epoch 3: Train Loss 0.705466 |  Val Loss 0.691585
Epoch 4: Train Loss 0.699055 |  Val Loss 0.686501
Epoch 5: Train Loss 0.693635 |  Val Loss 0.682374
Epoch 6: Train Loss 0.689176 |  Val Loss 0.679154
Epoch 7: Train Loss 0.685620 |  Val Loss 0.676738
Epoch 8: Train Loss 0.682883 |  Val Loss 0.674988
Epoch 9: Train Loss 0.680847 |  Val Loss 0.673775
Epoch 10: Train Loss 0.679376 |  Val Loss 0.672956
Epoch 11: Train Loss 0.678321 |  Val Loss 0.672384
Epoch 12: Train Loss 0.677532 |  Val Loss 0.671895
Epoch 13: Train Loss 0.676879 |  Val Loss 0.671379
Epoch 14: Train Loss 0.676241 |  Val Loss 0.670751
Epoch 15: Train Loss 0.675527 |  Val Loss 0.669954
Epoch 16: Train Loss 0.674681 |  Val Loss 0.668958
Epoch 17: Train Loss 0.673671 |  Val Lo

[I 2025-01-04 16:03:31,220] Trial 0 finished with value: 0.6681531047810609 and parameters: {'n_trees': 96, 'n_selected': 16, 'n_layers': 1, 'mask_type': 'entmax'}. Best is trial 0 with value: 0.6681531047810609.


Epoch 393: Train Loss 0.255423 |  Val Loss 0.375953
Epoch 394: Train Loss 0.254535 |  Val Loss 0.375881
Epoch 395: Train Loss 0.253650 |  Val Loss 0.375817
Epoch 396: Train Loss 0.252770 |  Val Loss 0.375760
Epoch 397: Train Loss 0.251892 |  Val Loss 0.375708
Epoch 398: Train Loss 0.251021 |  Val Loss 0.375653
Epoch 399: Train Loss 0.250153 |  Val Loss 0.375590
Epoch 400: Train Loss 0.249292 |  Val Loss 0.375537
Epoch 401: Train Loss 0.248437 |  Val Loss 0.375496
Epoch 402: Train Loss 0.247590 |  Val Loss 0.375467
Epoch 403: Train Loss 0.246744 |  Val Loss 0.375446
Epoch 404: Train Loss 0.245903 |  Val Loss 0.375440
Epoch 405: Train Loss 0.245062 |  Val Loss 0.375458
Epoch 406: Train Loss 0.244223 |  Val Loss 0.375490
Epoch 407: Train Loss 0.243386 |  Val Loss 0.375526
Epoch 408: Train Loss 0.242551 |  Val Loss 0.375566
Epoch 409: Train Loss 0.241719 |  Val Loss 0.375601
Epoch 410: Train Loss 0.240890 |  Val Loss 0.375636
Epoch 411: Train Loss 0.240062 |  Val Loss 0.375672
Epoch 412: T

[I 2025-01-04 16:03:31,859] Trial 1 finished with value: 0.6681531047810609 and parameters: {'n_trees': 8, 'n_selected': 24, 'n_layers': 4, 'mask_type': 'entmax'}. Best is trial 0 with value: 0.6681531047810609.


...

Epoch 303: Train Loss 0.026094 |  Val Loss 0.267384
Epoch 304: Train Loss 0.025809 |  Val Loss 0.267271
Epoch 305: Train Loss 0.025543 |  Val Loss 0.266866
Epoch 306: Train Loss 0.025268 |  Val Loss 0.266408
Epoch 307: Train Loss 0.024999 |  Val Loss 0.266683
Epoch 308: Train Loss 0.024740 |  Val Loss 0.267169
Epoch 309: Train Loss 0.024473 |  Val Loss 0.267368
Epoch 310: Train Loss 0.024221 |  Val Loss 0.267162
Epoch 311: Train Loss 0.023971 |  Val Loss 0.267028
Epoch 312: Train Loss 0.023716 |  Val Loss 0.267114
Epoch 313: Train Loss 0.023477 |  Val Loss 0.266926
Epoch 314: Train Loss 0.023227 |  Val Loss 0.266978
Epoch 315: Train Loss 0.022995 |  Val Loss 0.266939
Epoch 316: Train Loss 0.022763 |  Val Loss 0.267075
Epoch 317: Train Loss 0.022524 |  Val Loss 0.267179
Validation loss has not improved for 10 steps!
Early stopping applies.
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.690389 |  Val Loss 0.686252
Epoch 1: Train Loss 0.685790 |  Val Loss 0.681526
Epoch 2:

[I 2025-01-04 16:04:12,044] Trial 13 finished with value: 0.8017837257372731 and parameters: {'n_trees': 64, 'n_selected': 4, 'n_layers': 5, 'mask_type': 'sparsemax'}. Best is trial 3 with value: 0.9354143466934853.


Epoch 324: Train Loss 0.079454 |  Val Loss 0.270963
Validation loss has not improved for 10 steps!
Early stopping applies.
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.803403 |  Val Loss 0.783003
Epoch 1: Train Loss 0.786605 |  Val Loss 0.771474
Epoch 2: Train Loss 0.772538 |  Val Loss 0.758065
Epoch 3: Train Loss 0.759801 |  Val Loss 0.746049
Epoch 4: Train Loss 0.748745 |  Val Loss 0.734881
Epoch 5: Train Loss 0.737837 |  Val Loss 0.723797
Epoch 6: Train Loss 0.727245 |  Val Loss 0.713798
Epoch 7: Train Loss 0.717107 |  Val Loss 0.704286
Epoch 8: Train Loss 0.707428 |  Val Loss 0.695683
Epoch 9: Train Loss 0.698291 |  Val Loss 0.688029
Epoch 10: Train Loss 0.689516 |  Val Loss 0.680912
Epoch 11: Train Loss 0.681084 |  Val Loss 0.673886
Epoch 12: Train Loss 0.672904 |  Val Loss 0.667017
Epoch 13: Train Loss 0.664979 |  Val Loss 0.660113
Epoch 14: Train Loss 0.657356 |  Val Loss 0.653709
Epoch 15: Train Loss 0.650095 |  Val Loss 0.647031
Epoch 16: Train Loss 0.643060 

[I 2025-01-04 16:04:14,301] Trial 14 finished with value: 0.8744746321952062 and parameters: {'n_trees': 40, 'n_selected': 8, 'n_layers': 3, 'mask_type': 'sparsemax'}. Best is trial 3 with value: 0.9354143466934853.


Epoch 163: Train Loss 0.090856 |  Val Loss 0.290230
Epoch 164: Train Loss 0.090061 |  Val Loss 0.282876
Epoch 165: Train Loss 0.088332 |  Val Loss 0.277499
Epoch 166: Train Loss 0.087238 |  Val Loss 0.276143
Epoch 167: Train Loss 0.086119 |  Val Loss 0.272758
Epoch 168: Train Loss 0.084806 |  Val Loss 0.277097
Epoch 169: Train Loss 0.083648 |  Val Loss 0.283057
Epoch 170: Train Loss 0.082585 |  Val Loss 0.281902
Epoch 171: Train Loss 0.081317 |  Val Loss 0.278241
Epoch 172: Train Loss 0.080311 |  Val Loss 0.274097
Epoch 173: Train Loss 0.079168 |  Val Loss 0.274099
Epoch 174: Train Loss 0.078066 |  Val Loss 0.276652
Epoch 175: Train Loss 0.077068 |  Val Loss 0.275101
Epoch 176: Train Loss 0.075965 |  Val Loss 0.274159
Epoch 177: Train Loss 0.074984 |  Val Loss 0.274904
Epoch 178: Train Loss 0.073959 |  Val Loss 0.275624
Validation loss has not improved for 10 steps!
Early stopping applies.
Best hyperparameters: {'n_trees': 88, 'n_selected': 4, 'n_layers': 3, 'mask_type': 'sparsemax'}
O

In [31]:
start_time = time.time()
XII_150_pcc75_results_df = train_with_best_hyperparameters(datasets, 'XII_150_pcc75')
elapsed_time = time.time() - start_time
print(f"Elapsed time: {elapsed_time:.2f} seconds")

[I 2025-01-04 16:05:03,834] A new study created in memory with name: no-name-56c9f8cb-6f5c-4b7f-9db0-04c6f65a1915


Currently training NCART model with dataset key: XII_150_pcc75
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.724247 |  Val Loss 0.729229
Epoch 1: Train Loss 0.711323 |  Val Loss 0.718114
Epoch 2: Train Loss 0.700314 |  Val Loss 0.707873
Epoch 3: Train Loss 0.690035 |  Val Loss 0.699785
Epoch 4: Train Loss 0.680884 |  Val Loss 0.689712
Epoch 5: Train Loss 0.672879 |  Val Loss 0.683194
Epoch 6: Train Loss 0.665585 |  Val Loss 0.676437
Epoch 7: Train Loss 0.659135 |  Val Loss 0.668185
Epoch 8: Train Loss 0.652884 |  Val Loss 0.660836
Epoch 9: Train Loss 0.647273 |  Val Loss 0.654806
Epoch 10: Train Loss 0.642060 |  Val Loss 0.649376
Epoch 11: Train Loss 0.637096 |  Val Loss 0.643841
Epoch 12: Train Loss 0.632182 |  Val Loss 0.638641
Epoch 13: Train Loss 0.627197 |  Val Loss 0.633533
Epoch 14: Train Loss 0.622119 |  Val Loss 0.628633
Epoch 15: Train Loss 0.616962 |  Val Loss 0.623849
Epoch 16: Train Loss 0.611851 |  Val Loss 0.618810
Epoch 17: Train Loss 0.606649 |  Val Lo

[I 2025-01-04 16:05:06,547] Trial 0 finished with value: 0.8017837257372731 and parameters: {'n_trees': 128, 'n_selected': 12, 'n_layers': 4, 'mask_type': 'sparsemax'}. Best is trial 0 with value: 0.8017837257372731.


Epoch 206: Train Loss 0.017816 |  Val Loss 0.188580
Epoch 207: Train Loss 0.017604 |  Val Loss 0.188506
Validation loss has not improved for 10 steps!
Early stopping applies.
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 1.167930 |  Val Loss 1.063354
Epoch 1: Train Loss 1.037191 |  Val Loss 0.947884
Epoch 2: Train Loss 0.921343 |  Val Loss 0.854387
Epoch 3: Train Loss 0.823007 |  Val Loss 0.776666
Epoch 4: Train Loss 0.739850 |  Val Loss 0.710778
Epoch 5: Train Loss 0.668800 |  Val Loss 0.658146
Epoch 6: Train Loss 0.611061 |  Val Loss 0.618132
Epoch 7: Train Loss 0.565247 |  Val Loss 0.589725
Epoch 8: Train Loss 0.530649 |  Val Loss 0.568735
Epoch 9: Train Loss 0.506756 |  Val Loss 0.555132
Epoch 10: Train Loss 0.489769 |  Val Loss 0.547147
Epoch 11: Train Loss 0.477389 |  Val Loss 0.542525
Epoch 12: Train Loss 0.468014 |  Val Loss 0.539580
Epoch 13: Train Loss 0.459230 |  Val Loss 0.536749
Epoch 14: Train Loss 0.448888 |  Val Loss 0.532851
Epoch 15: Train Loss 0.438135

[I 2025-01-04 16:05:07,576] Trial 1 finished with value: 0.8017837257372731 and parameters: {'n_trees': 40, 'n_selected': 32, 'n_layers': 6, 'mask_type': 'sparsemax'}. Best is trial 0 with value: 0.8017837257372731.


...

Epoch 131: Train Loss 0.060286 |  Val Loss 0.250592
Epoch 132: Train Loss 0.058601 |  Val Loss 0.249974
Epoch 133: Train Loss 0.057107 |  Val Loss 0.249888
Epoch 134: Train Loss 0.055579 |  Val Loss 0.249824
Epoch 135: Train Loss 0.054279 |  Val Loss 0.249198
Epoch 136: Train Loss 0.052742 |  Val Loss 0.249637
Epoch 137: Train Loss 0.051494 |  Val Loss 0.250330
Epoch 138: Train Loss 0.050105 |  Val Loss 0.249817
Epoch 139: Train Loss 0.048836 |  Val Loss 0.250313
Epoch 140: Train Loss 0.047637 |  Val Loss 0.250536
Epoch 141: Train Loss 0.046240 |  Val Loss 0.250818
Epoch 142: Train Loss 0.045263 |  Val Loss 0.249684
Epoch 143: Train Loss 0.043926 |  Val Loss 0.249543
Epoch 144: Train Loss 0.042992 |  Val Loss 0.251054
Epoch 145: Train Loss 0.041832 |  Val Loss 0.251614
Epoch 146: Train Loss 0.040771 |  Val Loss 0.251325
Validation loss has not improved for 10 steps!
Early stopping applies.
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 1.776186 |  Val Loss 1.562894
Epoch 

[I 2025-01-04 16:05:41,899] Trial 13 finished with value: 0.8666666666666667 and parameters: {'n_trees': 8, 'n_selected': 24, 'n_layers': 7, 'mask_type': 'entmax'}. Best is trial 6 with value: 0.8744746321952062.


Epoch 69: Train Loss 0.048766 |  Val Loss 0.272193
Epoch 70: Train Loss 0.047068 |  Val Loss 0.274888
Epoch 71: Train Loss 0.045435 |  Val Loss 0.275599
Epoch 72: Train Loss 0.043858 |  Val Loss 0.276004
Epoch 73: Train Loss 0.042345 |  Val Loss 0.276742
Epoch 74: Train Loss 0.040915 |  Val Loss 0.277248
Epoch 75: Train Loss 0.039561 |  Val Loss 0.276818
Epoch 76: Train Loss 0.038257 |  Val Loss 0.276122
Epoch 77: Train Loss 0.037011 |  Val Loss 0.275266
Epoch 78: Train Loss 0.035833 |  Val Loss 0.274756
Epoch 79: Train Loss 0.034711 |  Val Loss 0.274642
Validation loss has not improved for 10 steps!
Early stopping applies.
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.843258 |  Val Loss 0.822921
Epoch 1: Train Loss 0.778199 |  Val Loss 0.771638
Epoch 2: Train Loss 0.725802 |  Val Loss 0.730506
Epoch 3: Train Loss 0.683781 |  Val Loss 0.697399
Epoch 4: Train Loss 0.651533 |  Val Loss 0.671665
Epoch 5: Train Loss 0.628804 |  Val Loss 0.649450
Epoch 6: Train Loss 0.61431

[I 2025-01-04 16:05:43,193] Trial 14 finished with value: 0.8666666666666667 and parameters: {'n_trees': 96, 'n_selected': 28, 'n_layers': 3, 'mask_type': 'sparsemax'}. Best is trial 6 with value: 0.8744746321952062.


Epoch 91: Train Loss 0.027922 |  Val Loss 0.242378
Epoch 92: Train Loss 0.026961 |  Val Loss 0.243312
Epoch 93: Train Loss 0.026080 |  Val Loss 0.240473
Epoch 94: Train Loss 0.025246 |  Val Loss 0.241483
Epoch 95: Train Loss 0.024432 |  Val Loss 0.244437
Epoch 96: Train Loss 0.023661 |  Val Loss 0.243791
Epoch 97: Train Loss 0.022944 |  Val Loss 0.240607
Validation loss has not improved for 10 steps!
Early stopping applies.
Best hyperparameters: {'n_trees': 8, 'n_selected': 32, 'n_layers': 7, 'mask_type': 'sparsemax'}
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 1.723610 |  Val Loss 1.502685
Epoch 1: Train Loss 1.590485 |  Val Loss 1.383113
Epoch 2: Train Loss 1.458394 |  Val Loss 1.269352
Epoch 3: Train Loss 1.328896 |  Val Loss 1.161044
Epoch 4: Train Loss 1.205523 |  Val Loss 1.058727
Epoch 5: Train Loss 1.088397 |  Val Loss 0.961987
Epoch 6: Train Loss 0.980384 |  Val Loss 0.876063
Epoch 7: Train Loss 0.882778 |  Val Loss 0.800356
Epoch 8: Train Loss 0.795399 |  Val

In [32]:
start_time = time.time()
XII_100_nopcc_results_df = train_with_best_hyperparameters(datasets, 'XII_100_nopcc')
elapsed_time = time.time() - start_time
print(f"Elapsed time: {elapsed_time:.2f} seconds")

[I 2025-01-04 16:06:00,073] A new study created in memory with name: no-name-f384e31b-f9ae-4118-8107-322465765741


Currently training NCART model with dataset key: XII_100_nopcc
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.897474 |  Val Loss 0.805997
Epoch 1: Train Loss 0.789397 |  Val Loss 0.723676
Epoch 2: Train Loss 0.707524 |  Val Loss 0.652519
Epoch 3: Train Loss 0.637707 |  Val Loss 0.591558
Epoch 4: Train Loss 0.578520 |  Val Loss 0.539578
Epoch 5: Train Loss 0.530053 |  Val Loss 0.499550
Epoch 6: Train Loss 0.489440 |  Val Loss 0.467871
Epoch 7: Train Loss 0.455804 |  Val Loss 0.442324
Epoch 8: Train Loss 0.429268 |  Val Loss 0.421228
Epoch 9: Train Loss 0.407430 |  Val Loss 0.403106
Epoch 10: Train Loss 0.387525 |  Val Loss 0.387336
Epoch 11: Train Loss 0.368788 |  Val Loss 0.371649
Epoch 12: Train Loss 0.350768 |  Val Loss 0.356993
Epoch 13: Train Loss 0.334397 |  Val Loss 0.343878
Epoch 14: Train Loss 0.318356 |  Val Loss 0.328567
Epoch 15: Train Loss 0.302364 |  Val Loss 0.312712
Epoch 16: Train Loss 0.286077 |  Val Loss 0.295776
Epoch 17: Train Loss 0.269419 |  Val Lo

[I 2025-01-04 16:06:18,420] Trial 0 finished with value: 1.0 and parameters: {'n_trees': 120, 'n_selected': 28, 'n_layers': 7, 'mask_type': 'entmax'}. Best is trial 0 with value: 1.0.


Epoch 993: Train Loss 0.000169 |  Val Loss 0.000381
Epoch 994: Train Loss 0.000168 |  Val Loss 0.000380
Epoch 995: Train Loss 0.000168 |  Val Loss 0.000379
Epoch 996: Train Loss 0.000167 |  Val Loss 0.000378
Epoch 997: Train Loss 0.000167 |  Val Loss 0.000378
Epoch 998: Train Loss 0.000167 |  Val Loss 0.000377
Epoch 999: Train Loss 0.000166 |  Val Loss 0.000376
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.933478 |  Val Loss 0.855321
Epoch 1: Train Loss 0.837647 |  Val Loss 0.771664
Epoch 2: Train Loss 0.754589 |  Val Loss 0.699495
Epoch 3: Train Loss 0.683824 |  Val Loss 0.639979
Epoch 4: Train Loss 0.626220 |  Val Loss 0.585647
Epoch 5: Train Loss 0.577022 |  Val Loss 0.542557
Epoch 6: Train Loss 0.535315 |  Val Loss 0.505548
Epoch 7: Train Loss 0.500051 |  Val Loss 0.471775
Epoch 8: Train Loss 0.469151 |  Val Loss 0.447981
Epoch 9: Train Loss 0.443434 |  Val Loss 0.424921
Epoch 10: Train Loss 0.420973 |  Val Loss 0.404993
Epoch 11: Train Loss 0.400430 |  Val Loss 0.

[I 2025-01-04 16:06:38,329] Trial 1 finished with value: 1.0 and parameters: {'n_trees': 128, 'n_selected': 24, 'n_layers': 8, 'mask_type': 'entmax'}. Best is trial 0 with value: 1.0.


...

Epoch 989: Train Loss 0.000087 |  Val Loss 0.000505
Epoch 990: Train Loss 0.000086 |  Val Loss 0.000504
Epoch 991: Train Loss 0.000086 |  Val Loss 0.000504
Epoch 992: Train Loss 0.000086 |  Val Loss 0.000503
Epoch 993: Train Loss 0.000086 |  Val Loss 0.000502
Epoch 994: Train Loss 0.000086 |  Val Loss 0.000502
Epoch 995: Train Loss 0.000086 |  Val Loss 0.000501
Epoch 996: Train Loss 0.000085 |  Val Loss 0.000500
Epoch 997: Train Loss 0.000085 |  Val Loss 0.000499
Epoch 998: Train Loss 0.000085 |  Val Loss 0.000499
Epoch 999: Train Loss 0.000085 |  Val Loss 0.000498
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.712623 |  Val Loss 0.705181
Epoch 1: Train Loss 0.687123 |  Val Loss 0.686690
Epoch 2: Train Loss 0.672536 |  Val Loss 0.671064
Epoch 3: Train Loss 0.658122 |  Val Loss 0.657323
Epoch 4: Train Loss 0.643695 |  Val Loss 0.643477
Epoch 5: Train Loss 0.629902 |  Val Loss 0.630097
Epoch 6: Train Loss 0.616640 |  Val Loss 0.616668
Epoch 7: Train Loss 0.604221 |  Val L

[I 2025-01-04 16:09:33,308] Trial 13 finished with value: 1.0 and parameters: {'n_trees': 128, 'n_selected': 24, 'n_layers': 3, 'mask_type': 'entmax'}. Best is trial 0 with value: 1.0.


On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.746193 |  Val Loss 0.615065
Epoch 1: Train Loss 0.622284 |  Val Loss 0.550261
Epoch 2: Train Loss 0.548613 |  Val Loss 0.501446
Epoch 3: Train Loss 0.496752 |  Val Loss 0.474150
Epoch 4: Train Loss 0.460972 |  Val Loss 0.448206
Epoch 5: Train Loss 0.429120 |  Val Loss 0.415701
Epoch 6: Train Loss 0.398451 |  Val Loss 0.382525
Epoch 7: Train Loss 0.367759 |  Val Loss 0.354521
Epoch 8: Train Loss 0.339460 |  Val Loss 0.329837
Epoch 9: Train Loss 0.310958 |  Val Loss 0.314914
Epoch 10: Train Loss 0.283387 |  Val Loss 0.293530
Epoch 11: Train Loss 0.257668 |  Val Loss 0.280963
Epoch 12: Train Loss 0.235292 |  Val Loss 0.258188
Epoch 13: Train Loss 0.215127 |  Val Loss 0.258152
Epoch 14: Train Loss 0.196370 |  Val Loss 0.242536
Epoch 15: Train Loss 0.178836 |  Val Loss 0.230522
Epoch 16: Train Loss 0.162099 |  Val Loss 0.195312
Epoch 17: Train Loss 0.147282 |  Val Loss 0.185444
Epoch 18: Train Loss 0.133205 |  Val Loss 0.174521


[I 2025-01-04 16:09:35,885] Trial 14 finished with value: 0.9045340337332909 and parameters: {'n_trees': 56, 'n_selected': 32, 'n_layers': 8, 'mask_type': 'entmax'}. Best is trial 0 with value: 1.0.


Epoch 119: Train Loss 0.003371 |  Val Loss 0.019770
Validation loss has not improved for 10 steps!
Early stopping applies.
Best hyperparameters: {'n_trees': 120, 'n_selected': 28, 'n_layers': 7, 'mask_type': 'entmax'}
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.897474 |  Val Loss 0.805997
Epoch 1: Train Loss 0.789397 |  Val Loss 0.723676
Epoch 2: Train Loss 0.707524 |  Val Loss 0.652519
Epoch 3: Train Loss 0.637707 |  Val Loss 0.591558
Epoch 4: Train Loss 0.578520 |  Val Loss 0.539578
Epoch 5: Train Loss 0.530053 |  Val Loss 0.499550
Epoch 6: Train Loss 0.489440 |  Val Loss 0.467871
Epoch 7: Train Loss 0.455804 |  Val Loss 0.442324
Epoch 8: Train Loss 0.429268 |  Val Loss 0.421228
Epoch 9: Train Loss 0.407430 |  Val Loss 0.403106
Epoch 10: Train Loss 0.387525 |  Val Loss 0.387336
Epoch 11: Train Loss 0.368788 |  Val Loss 0.371649
Epoch 12: Train Loss 0.350768 |  Val Loss 0.356993
Epoch 13: Train Loss 0.334397 |  Val Loss 0.343878
Epoch 14: Train Loss 0.318356 |  Val 

In [33]:
start_time = time.time()
XII_100_pcc95_results_df = train_with_best_hyperparameters(datasets, 'XII_100_pcc95')
elapsed_time = time.time() - start_time
print(f"Elapsed time: {elapsed_time:.2f} seconds")

[I 2025-01-04 16:10:28,868] A new study created in memory with name: no-name-cf0989db-47ed-4de4-abbe-8590fe711f60


Currently training NCART model with dataset key: XII_100_pcc95
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.694930 |  Val Loss 0.685463
Epoch 1: Train Loss 0.661983 |  Val Loss 0.658292
Epoch 2: Train Loss 0.637472 |  Val Loss 0.636593
Epoch 3: Train Loss 0.615969 |  Val Loss 0.615689
Epoch 4: Train Loss 0.596584 |  Val Loss 0.595065
Epoch 5: Train Loss 0.578680 |  Val Loss 0.576430
Epoch 6: Train Loss 0.562469 |  Val Loss 0.557876
Epoch 7: Train Loss 0.547202 |  Val Loss 0.539955
Epoch 8: Train Loss 0.532411 |  Val Loss 0.524284
Epoch 9: Train Loss 0.518034 |  Val Loss 0.509141
Epoch 10: Train Loss 0.504050 |  Val Loss 0.495661
Epoch 11: Train Loss 0.490128 |  Val Loss 0.482297
Epoch 12: Train Loss 0.476398 |  Val Loss 0.469981
Epoch 13: Train Loss 0.462573 |  Val Loss 0.458118
Epoch 14: Train Loss 0.449200 |  Val Loss 0.447702
Epoch 15: Train Loss 0.435990 |  Val Loss 0.436765
Epoch 16: Train Loss 0.423066 |  Val Loss 0.426316
Epoch 17: Train Loss 0.410519 |  Val Lo

[I 2025-01-04 16:10:30,912] Trial 0 finished with value: 0.9045340337332909 and parameters: {'n_trees': 64, 'n_selected': 12, 'n_layers': 8, 'mask_type': 'sparsemax'}. Best is trial 0 with value: 0.9045340337332909.


Epoch 101: Train Loss 0.049375 |  Val Loss 0.111457
Epoch 102: Train Loss 0.048457 |  Val Loss 0.111279
Epoch 103: Train Loss 0.047549 |  Val Loss 0.110248
Epoch 104: Train Loss 0.046659 |  Val Loss 0.109237
Epoch 105: Train Loss 0.045801 |  Val Loss 0.108232
Validation loss has not improved for 10 steps!
Early stopping applies.
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.932278 |  Val Loss 0.842705
Epoch 1: Train Loss 0.854086 |  Val Loss 0.778158
Epoch 2: Train Loss 0.785121 |  Val Loss 0.722439
Epoch 3: Train Loss 0.724222 |  Val Loss 0.671428
Epoch 4: Train Loss 0.671459 |  Val Loss 0.625256
Epoch 5: Train Loss 0.625953 |  Val Loss 0.591929
Epoch 6: Train Loss 0.587667 |  Val Loss 0.556464
Epoch 7: Train Loss 0.555770 |  Val Loss 0.528913
Epoch 8: Train Loss 0.530068 |  Val Loss 0.505798
Epoch 9: Train Loss 0.509657 |  Val Loss 0.491565
Epoch 10: Train Loss 0.493629 |  Val Loss 0.474805
Epoch 11: Train Loss 0.480663 |  Val Loss 0.460943
Epoch 12: Train Loss 0.470

[I 2025-01-04 16:10:41,730] Trial 1 finished with value: 1.0 and parameters: {'n_trees': 48, 'n_selected': 24, 'n_layers': 3, 'mask_type': 'sparsemax'}. Best is trial 1 with value: 1.0.


...

Epoch 253: Train Loss 0.006980 |  Val Loss 0.054328
Epoch 254: Train Loss 0.006921 |  Val Loss 0.054337
Validation loss has not improved for 10 steps!
Early stopping applies.
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.770509 |  Val Loss 0.725966
Epoch 1: Train Loss 0.753777 |  Val Loss 0.710264
Epoch 2: Train Loss 0.737664 |  Val Loss 0.695643
Epoch 3: Train Loss 0.721987 |  Val Loss 0.682165
Epoch 4: Train Loss 0.707692 |  Val Loss 0.670971
Epoch 5: Train Loss 0.696536 |  Val Loss 0.660552
Epoch 6: Train Loss 0.686251 |  Val Loss 0.651614
Epoch 7: Train Loss 0.676305 |  Val Loss 0.642575
Epoch 8: Train Loss 0.666932 |  Val Loss 0.634110
Epoch 9: Train Loss 0.657978 |  Val Loss 0.625919
Epoch 10: Train Loss 0.649282 |  Val Loss 0.618115
Epoch 11: Train Loss 0.641120 |  Val Loss 0.611146
Epoch 12: Train Loss 0.633401 |  Val Loss 0.604445
Epoch 13: Train Loss 0.625897 |  Val Loss 0.597912
Epoch 14: Train Loss 0.618813 |  Val Loss 0.592766
Epoch 15: Train Loss 0.612080

[I 2025-01-04 16:12:18,316] Trial 13 finished with value: 1.0 and parameters: {'n_trees': 112, 'n_selected': 12, 'n_layers': 3, 'mask_type': 'sparsemax'}. Best is trial 1 with value: 1.0.



Epoch 996: Train Loss 0.000640 |  Val Loss 0.004633
Epoch 997: Train Loss 0.000639 |  Val Loss 0.004625
Epoch 998: Train Loss 0.000637 |  Val Loss 0.004620
Epoch 999: Train Loss 0.000636 |  Val Loss 0.004616
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.957833 |  Val Loss 0.825977
Epoch 1: Train Loss 0.876668 |  Val Loss 0.760981
Epoch 2: Train Loss 0.804248 |  Val Loss 0.698218
Epoch 3: Train Loss 0.740805 |  Val Loss 0.642765
Epoch 4: Train Loss 0.685258 |  Val Loss 0.599895
Epoch 5: Train Loss 0.637658 |  Val Loss 0.561985
Epoch 6: Train Loss 0.597171 |  Val Loss 0.530984
Epoch 7: Train Loss 0.563172 |  Val Loss 0.506883
Epoch 8: Train Loss 0.535233 |  Val Loss 0.488255
Epoch 9: Train Loss 0.512333 |  Val Loss 0.472501
Epoch 10: Train Loss 0.493767 |  Val Loss 0.459853
Epoch 11: Train Loss 0.479010 |  Val Loss 0.450459
Epoch 12: Train Loss 0.466953 |  Val Loss 0.441584
Epoch 13: Train Loss 0.456982 |  Val Loss 0.430790
Epoch 14: Train Loss 0.446876 |  Val Loss 0.42

[I 2025-01-04 16:12:32,581] Trial 14 finished with value: 1.0 and parameters: {'n_trees': 40, 'n_selected': 24, 'n_layers': 5, 'mask_type': 'entmax'}. Best is trial 1 with value: 1.0.


Epoch 997: Train Loss 0.000152 |  Val Loss 0.001002
Epoch 998: Train Loss 0.000152 |  Val Loss 0.001001
Epoch 999: Train Loss 0.000152 |  Val Loss 0.000999
Best hyperparameters: {'n_trees': 48, 'n_selected': 24, 'n_layers': 3, 'mask_type': 'sparsemax'}
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.932278 |  Val Loss 0.842705
Epoch 1: Train Loss 0.854086 |  Val Loss 0.778158
Epoch 2: Train Loss 0.785121 |  Val Loss 0.722439
Epoch 3: Train Loss 0.724222 |  Val Loss 0.671428
Epoch 4: Train Loss 0.671459 |  Val Loss 0.625256
Epoch 5: Train Loss 0.625953 |  Val Loss 0.591929
Epoch 6: Train Loss 0.587667 |  Val Loss 0.556464
Epoch 7: Train Loss 0.555770 |  Val Loss 0.528913
Epoch 8: Train Loss 0.530068 |  Val Loss 0.505798
Epoch 9: Train Loss 0.509657 |  Val Loss 0.491565
Epoch 10: Train Loss 0.493629 |  Val Loss 0.474805
Epoch 11: Train Loss 0.480663 |  Val Loss 0.460943
Epoch 12: Train Loss 0.470325 |  Val Loss 0.448885
Epoch 13: Train Loss 0.461108 |  Val Loss 0.435281
Ep

In [34]:
start_time = time.time()
XII_100_pcc75_results_df = train_with_best_hyperparameters(datasets, 'XII_100_pcc75')
elapsed_time = time.time() - start_time
print(f"Elapsed time: {elapsed_time:.2f} seconds")

[I 2025-01-04 16:13:10,138] A new study created in memory with name: no-name-58f5878c-9870-4965-98fc-3ed662317d88


Currently training NCART model with dataset key: XII_100_pcc75
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.696809 |  Val Loss 0.692539
Epoch 1: Train Loss 0.696576 |  Val Loss 0.692321
Epoch 2: Train Loss 0.696347 |  Val Loss 0.692103
Epoch 3: Train Loss 0.696121 |  Val Loss 0.691888
Epoch 4: Train Loss 0.695897 |  Val Loss 0.691673
Epoch 5: Train Loss 0.695676 |  Val Loss 0.691459
Epoch 6: Train Loss 0.695458 |  Val Loss 0.691246
Epoch 7: Train Loss 0.695241 |  Val Loss 0.691034
Epoch 8: Train Loss 0.695027 |  Val Loss 0.690819
Epoch 9: Train Loss 0.694815 |  Val Loss 0.690605
Epoch 10: Train Loss 0.694604 |  Val Loss 0.690392
Epoch 11: Train Loss 0.694394 |  Val Loss 0.690179
Epoch 12: Train Loss 0.694185 |  Val Loss 0.689966
Epoch 13: Train Loss 0.693977 |  Val Loss 0.689754
Epoch 14: Train Loss 0.693769 |  Val Loss 0.689545
Epoch 15: Train Loss 0.693559 |  Val Loss 0.689335
Epoch 16: Train Loss 0.693349 |  Val Loss 0.689123
Epoch 17: Train Loss 0.693138 |  Val Lo

[I 2025-01-04 16:13:17,681] Trial 0 finished with value: 0.8 and parameters: {'n_trees': 64, 'n_selected': 4, 'n_layers': 1, 'mask_type': 'entmax'}. Best is trial 0 with value: 0.8.


Epoch 997: Train Loss 0.187581 |  Val Loss 0.263010
Epoch 998: Train Loss 0.187295 |  Val Loss 0.262907
Epoch 999: Train Loss 0.187011 |  Val Loss 0.262830
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.992143 |  Val Loss 0.903950
Epoch 1: Train Loss 0.912659 |  Val Loss 0.837434
Epoch 2: Train Loss 0.842551 |  Val Loss 0.786210
Epoch 3: Train Loss 0.783106 |  Val Loss 0.734531
Epoch 4: Train Loss 0.732861 |  Val Loss 0.687747
Epoch 5: Train Loss 0.688784 |  Val Loss 0.647067
Epoch 6: Train Loss 0.649960 |  Val Loss 0.607227
Epoch 7: Train Loss 0.617408 |  Val Loss 0.574977
Epoch 8: Train Loss 0.591158 |  Val Loss 0.549412
Epoch 9: Train Loss 0.570452 |  Val Loss 0.529794
Epoch 10: Train Loss 0.554547 |  Val Loss 0.515224
Epoch 11: Train Loss 0.542424 |  Val Loss 0.505366
Epoch 12: Train Loss 0.532540 |  Val Loss 0.498790
Epoch 13: Train Loss 0.526147 |  Val Loss 0.492419
Epoch 14: Train Loss 0.519940 |  Val Loss 0.484973
Epoch 15: Train Loss 0.514541 |  Val Loss 0.4834

[I 2025-01-04 16:13:19,316] Trial 1 finished with value: 0.9045340337332909 and parameters: {'n_trees': 32, 'n_selected': 24, 'n_layers': 7, 'mask_type': 'entmax'}. Best is trial 1 with value: 0.9045340337332909.


...

Epoch 542: Train Loss 0.002972 |  Val Loss 0.093206
Epoch 543: Train Loss 0.002960 |  Val Loss 0.093253
Epoch 544: Train Loss 0.002947 |  Val Loss 0.093241
Epoch 545: Train Loss 0.002935 |  Val Loss 0.093228
Epoch 546: Train Loss 0.002923 |  Val Loss 0.093273
Epoch 547: Train Loss 0.002910 |  Val Loss 0.093230
Epoch 548: Train Loss 0.002898 |  Val Loss 0.093170
Epoch 549: Train Loss 0.002886 |  Val Loss 0.093240
Epoch 550: Train Loss 0.002874 |  Val Loss 0.093323
Epoch 551: Train Loss 0.002862 |  Val Loss 0.093405
Validation loss has not improved for 10 steps!
Early stopping applies.
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 0.712296 |  Val Loss 0.709814
Epoch 1: Train Loss 0.709397 |  Val Loss 0.708383
Epoch 2: Train Loss 0.706486 |  Val Loss 0.706293
Epoch 3: Train Loss 0.704035 |  Val Loss 0.704252
Epoch 4: Train Loss 0.701686 |  Val Loss 0.702026
Epoch 5: Train Loss 0.699333 |  Val Loss 0.699688
Epoch 6: Train Loss 0.697010 |  Val Loss 0.697114
Epoch 7: Train Los

[I 2025-01-04 16:14:19,113] Trial 13 finished with value: 0.9045340337332909 and parameters: {'n_trees': 72, 'n_selected': 4, 'n_layers': 4, 'mask_type': 'sparsemax'}. Best is trial 3 with value: 1.0.


Epoch 675: Train Loss 0.013759 |  Val Loss 0.096965
Epoch 676: Train Loss 0.013702 |  Val Loss 0.096135
Epoch 677: Train Loss 0.013645 |  Val Loss 0.096553
Epoch 678: Train Loss 0.013589 |  Val Loss 0.096184
Epoch 679: Train Loss 0.013533 |  Val Loss 0.096546
Validation loss has not improved for 10 steps!
Early stopping applies.
On Device:  cuda:0
Binary classification
Epoch 0: Train Loss 1.316504 |  Val Loss 1.318993
Epoch 1: Train Loss 1.289190 |  Val Loss 1.291541
Epoch 2: Train Loss 1.262619 |  Val Loss 1.267441
Epoch 3: Train Loss 1.236440 |  Val Loss 1.243307
Epoch 4: Train Loss 1.210655 |  Val Loss 1.219490
Epoch 5: Train Loss 1.185405 |  Val Loss 1.196161
Epoch 6: Train Loss 1.160502 |  Val Loss 1.172768
Epoch 7: Train Loss 1.136104 |  Val Loss 1.150198
Epoch 8: Train Loss 1.112009 |  Val Loss 1.128795
Epoch 9: Train Loss 1.088377 |  Val Loss 1.107925
Epoch 10: Train Loss 1.065159 |  Val Loss 1.087515
Epoch 11: Train Loss 1.042382 |  Val Loss 1.067945
Epoch 12: Train Loss 1.020

[I 2025-01-04 16:14:22,985] Trial 14 finished with value: 0.9045340337332909 and parameters: {'n_trees': 8, 'n_selected': 16, 'n_layers': 2, 'mask_type': 'sparsemax'}. Best is trial 3 with value: 1.0.


Epoch 393: Train Loss 0.023006 |  Val Loss 0.146410
Epoch 394: Train Loss 0.022767 |  Val Loss 0.146047
Epoch 395: Train Loss 0.022581 |  Val Loss 0.146498
Epoch 396: Train Loss 0.022291 |  Val Loss 0.146983
Epoch 397: Train Loss 0.022023 |  Val Loss 0.146389
Epoch 398: Train Loss 0.021797 |  Val Loss 0.144919
Epoch 399: Train Loss 0.021557 |  Val Loss 0.145027
Epoch 400: Train Loss 0.021317 |  Val Loss 0.145539
Epoch 401: Train Loss 0.021091 |  Val Loss 0.146075
Epoch 402: Train Loss 0.020858 |  Val Loss 0.146184
Epoch 403: Train Loss 0.020665 |  Val Loss 0.144996
Epoch 404: Train Loss 0.020420 |  Val Loss 0.143327
Epoch 405: Train Loss 0.020236 |  Val Loss 0.144067
Epoch 406: Train Loss 0.020056 |  Val Loss 0.145802
Epoch 407: Train Loss 0.019814 |  Val Loss 0.147385
Epoch 408: Train Loss 0.019584 |  Val Loss 0.148172
Epoch 409: Train Loss 0.019399 |  Val Loss 0.146688
Epoch 410: Train Loss 0.019212 |  Val Loss 0.143678
Epoch 411: Train Loss 0.018977 |  Val Loss 0.143964
Epoch 412: T

In [35]:
print("Tuned Model:")
print('\n---------------------------------------------------------------------\n')
view_results_df(XII_all_nopcc_results_df, 'XII_all_nopcc')
print('\n---------------------------------------------------------------------\n')
view_results_df(XII_all_pcc95_results_df, 'XII_all_pcc95')
print('\n---------------------------------------------------------------------\n')
view_results_df(XII_all_nopcc_results_df, 'XII_all_pcc75')
print('\n---------------------------------------------------------------------\n')
view_results_df(XII_200_nopcc_results_df, 'XII_200_nopcc')
print('\n---------------------------------------------------------------------\n')
view_results_df(XII_200_pcc95_results_df, 'XII_200_pcc95')
print('\n---------------------------------------------------------------------\n')
view_results_df(XII_200_nopcc_results_df, 'XII_200_pcc75')
print('\n---------------------------------------------------------------------\n')
view_results_df(XII_150_nopcc_results_df, 'XII_150_nopcc')
print('\n---------------------------------------------------------------------\n')
view_results_df(XII_150_pcc95_results_df, 'XII_150_pcc95')
print('\n---------------------------------------------------------------------\n')
view_results_df(XII_150_nopcc_results_df, 'XII_150_pcc75')
print('\n---------------------------------------------------------------------\n')
view_results_df(XII_100_nopcc_results_df, 'XII_100_nopcc')
print('\n---------------------------------------------------------------------\n')
view_results_df(XII_100_pcc95_results_df, 'XII_100_pcc95')
print('\n---------------------------------------------------------------------\n')
view_results_df(XII_100_nopcc_results_df, 'XII_100_pcc75')
print('\n---------------------------------------------------------------------\n')


Tuned Model:

---------------------------------------------------------------------

10-fold cross validation results for results_df with key: XII_all_nopcc
Fold 0, Accuracy: 0.898, MCC: 0.797
Fold 1, Accuracy: 0.837, MCC: 0.673
Fold 2, Accuracy: 0.918, MCC: 0.840
Fold 3, Accuracy: 0.878, MCC: 0.755
Fold 4, Accuracy: 0.898, MCC: 0.796
Fold 5, Accuracy: 0.898, MCC: 0.801
Fold 6, Accuracy: 0.551, MCC: 0.250
Fold 7, Accuracy: 0.938, MCC: 0.876
Fold 8, Accuracy: 0.792, MCC: 0.583
Fold 9, Accuracy: 0.521, MCC: 0.068

---------------------------------------------------------------------

10-fold cross validation results for results_df with key: XII_all_pcc95
Fold 0, Accuracy: 0.898, MCC: 0.797
Fold 1, Accuracy: 0.816, MCC: 0.633
Fold 2, Accuracy: 0.918, MCC: 0.840
Fold 3, Accuracy: 0.857, MCC: 0.719
Fold 4, Accuracy: 0.878, MCC: 0.755
Fold 5, Accuracy: 0.837, MCC: 0.673
Fold 6, Accuracy: 0.796, MCC: 0.594
Fold 7, Accuracy: 0.896, MCC: 0.798
Fold 8, Accuracy: 0.729, MCC: 0.459
Fold 9, Accurac